In [1]:
import pandas as pd
import numpy as np
import pickle

from sklearn.linear_model import LinearRegression
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn import metrics
from sklearn.model_selection import cross_validate
from sklearn.model_selection import cross_val_score
from sklearn.tree import export_graphviz
from sklearn.neighbors import KNeighborsRegressor
from sklearn.neural_network import MLPRegressor
import matplotlib.pyplot as plt
%matplotlib inline

import warnings
import time

In [2]:
#!/usr/bin/env python
# coding: utf-8

# ## Analysis of Random Sample of 1 million leavetimes merged with trips data

# In[2]:


df1 = pd.read_csv('../../data/leavetimes_trips_1e6.csv',sep=',')


# In[3]:


df1.head()

Unnamed: 0 DATASOURCE        DAYOFSERVICE   TRIPID  PROGRNUMBER  \
0           0         DB  25-AUG-18 00:00:00  7329034           32   
1           1         DB  31-MAY-18 00:00:00  6847697           13   
2           2         DB  26-MAY-18 00:00:00  6780534           14   
3           3         DB  23-APR-18 00:00:00  6635422            7   
4           4         DB  06-APR-18 00:00:00  6606411           33   

   STOPPOINTID  PLANNEDTIME_ARR  PLANNEDTIME_DEP  ACTUALTIME_ARR  \
0          609            46010            46010           45900   
1          847            33619            33619           33604   
2         4758            57703            57703           57898   
3         7030            27325            27325           27474   
4         1453            85482            85482           86219   

   ACTUALTIME_DEP  ...  NOTE_x  LINEID  ROUTEID  DIRECTION   BASIN  TENDERLOT  \
0           45900  ...     NaN     29A   29A_15          2  BasDef        NaN   
1           33616  ...     NaN     145  145_102          1  BasDef        NaN   
2           57917  ...     NaN      49    49_28          2  BasDef        NaN   
3           27511  ...     NaN     39A   39A_43          2  BasDef        NaN   
4           86219  ...     NaN     123   123_36          2  BasDef        NaN   

   SUPPRESSED_y JUSTIFICATIONID_y        LASTUPDATE_y     NOTE_y  
0           NaN               NaN  03-SEP-18 10:39:32  ,2478282,  
1           NaN               NaN  14-JUN-18 14:04:06  ,3272689,  
2           NaN               NaN  14-JUN-18 13:12:56  ,1726258,  
3           NaN               NaN  13-JUN-18 08:27:05  ,2424410,  
4           NaN               NaN  18-APR-18 10:49:06  ,3222191,  

[5 rows x 28 columns]

In [3]:

# In[4]:


df1.drop('Unnamed: 0',axis=1,inplace=True)


# In[5]:


# dtypes 
df1['DATASOURCE'] = df1['DATASOURCE'].astype('category')
df1['DAYOFSERVICE'] = df1['DAYOFSERVICE'].astype('datetime64')
df1['TRIPID'] = df1['TRIPID'].astype('object')
df1['PROGRNUMBER'] = df1['PROGRNUMBER'].astype('category')
df1['STOPPOINTID'] = df1['STOPPOINTID'].astype('category')
df1['VEHICLEID'] = df1['VEHICLEID'].astype('object')
df1['SUPPRESSED_x'] = df1['SUPPRESSED_x'].astype('category')
df1['JUSTIFICATIONID_x'] = df1['JUSTIFICATIONID_x'].astype('category')
df1['DIRECTION'] = df1['DIRECTION'].astype('category')
df1['SUPPRESSED_y'] = df1['SUPPRESSED_y'].astype('category')
df1['JUSTIFICATIONID_y'] = df1['JUSTIFICATIONID_y'].astype('category')
df1['TENDERLOT'] = df1['TENDERLOT'].astype('category')
df1['NOTE_x'] = df1['NOTE_x'].astype('category')
df1['PASSENGERS'] = df1['PASSENGERS'].astype('category')
df1['PASSENGERSIN'] = df1['PASSENGERSIN'].astype('category')
df1['PASSENGERSOUT'] = df1['PASSENGERSOUT'].astype('category')
df1['DISTANCE'] = df1['DISTANCE'].astype('category')
df1['NOTE_y'] = df1['DISTANCE'].astype('category')
df1['LASTUPDATE_x'] = df1['LASTUPDATE_x'].astype('datetime64')
df1['LASTUPDATE_y'] = df1['LASTUPDATE_y'].astype('datetime64')
df1['BASIN'] = df1['BASIN'].astype('category')
df1['LINEID'] = df1['LINEID'].astype('category')


# In[6]:


df1.dtypes


# In[7]:


categorical_columns = df1.select_dtypes('category').columns
numerical_columns = df1.select_dtypes('int64','float64').columns
object_columns = df1.select_dtypes('object').columns


# In[8]:


df1[categorical_columns].describe().T


# In[9]:


df1.drop(['PASSENGERS','PASSENGERSIN','PASSENGERSOUT','DISTANCE','NOTE_x'],axis=1,inplace=True)


# In[10]:


categorical_columns = df1.select_dtypes('category').columns


# In[11]:


df1[categorical_columns].describe().T


# In[12]:


df1.drop(['TENDERLOT','NOTE_y','BASIN','SUPPRESSED_y','JUSTIFICATIONID_y'],axis=1,inplace=True)


# In[13]:


categorical_columns = df1.select_dtypes('category').columns


# In[14]:


df1[categorical_columns].describe().T


# In[15]:


df1.head()


# In[16]:


df1_simple = df1.drop([
    'LASTUPDATE_y',
    'ROUTEID',
    'LASTUPDATE_x',
    'JUSTIFICATIONID_x',
    'SUPPRESSED_x',
    'ACTUALTIME_DEP',
    'VEHICLEID',
    'PLANNEDTIME_DEP'
],axis=1)

# df1_simple.drop(['PROGNUMBER','TRIPID'],axis=1,inplace=True)

# In[17]:


df1_simple.head()


# In[18]:


df1_simple.dtypes


# In[24]:


df1_simple['MONTH'] = df1_simple['DAYOFSERVICE'].dt.month.astype('category')
df1_simple['WEEKDAY'] = df1_simple['DAYOFSERVICE'].dt.weekday.astype('category')
# df1_simple.drop('DAYOFSERVICE',axis=1,inplace=True)


# In[25]:


df1_simple.head()


# In[26]:


df1_simple.dtypes


# In[ ]:


DATASOURCE               category
DAYOFSERVICE       datetime64[ns]
TRIPID                     object
PROGRNUMBER              category
STOPPOINTID              category
PLANNEDTIME_ARR             int64
ACTUALTIME_ARR              int64
LINEID                   category
DIRECTION                category
MONTH                    category
WEEKDAY                  category
dtype: object

In [4]:
df1_simple.head()

DATASOURCE DAYOFSERVICE   TRIPID PROGRNUMBER STOPPOINTID  PLANNEDTIME_ARR  \
0         DB   2018-08-25  7329034          32         609            46010   
1         DB   2018-05-31  6847697          13         847            33619   
2         DB   2018-05-26  6780534          14        4758            57703   
3         DB   2018-04-23  6635422           7        7030            27325   
4         DB   2018-04-06  6606411          33        1453            85482   

   ACTUALTIME_ARR LINEID DIRECTION MONTH WEEKDAY  
0           45900    29A         2     8       5  
1           33604    145         1     5       3  
2           57898     49         2     5       5  
3           27474    39A         2     4       0  
4           86219    123         2     4       4

In [5]:
# df1_simple['ARR_DELTA'] = df1_simple['PLANNEDTIME_ARR'] - df1_simple['ACTUALTIME_ARR']
# df1_simple.drop('ACTUALTIME_ARR',axis=1,inplace=True)

In [6]:
df1_simple.head()

DATASOURCE DAYOFSERVICE   TRIPID PROGRNUMBER STOPPOINTID  PLANNEDTIME_ARR  \
0         DB   2018-08-25  7329034          32         609            46010   
1         DB   2018-05-31  6847697          13         847            33619   
2         DB   2018-05-26  6780534          14        4758            57703   
3         DB   2018-04-23  6635422           7        7030            27325   
4         DB   2018-04-06  6606411          33        1453            85482   

   ACTUALTIME_ARR LINEID DIRECTION MONTH WEEKDAY  
0           45900    29A         2     8       5  
1           33604    145         1     5       3  
2           57898     49         2     5       5  
3           27474    39A         2     4       0  
4           86219    123         2     4       4

In [7]:
categorical_columns = df1_simple.select_dtypes('category').columns
df1_simple[categorical_columns].describe().T

count unique   top     freq
DATASOURCE   1000000      1    DB  1000000
PROGRNUMBER  1000000    105    13    18239
STOPPOINTID  1000000   4730  1478     1777
LINEID       1000000    130    40    37314
DIRECTION    1000000      2     2   505863
MONTH        1000000     12     1    90097
WEEKDAY      1000000      7     1   163043

## Multi-route Planning without Weather

In [8]:
df1 = pd.read_csv('../../data/leavetimes_trips_1e6.csv',sep=',')

df1.head()

Unnamed: 0 DATASOURCE        DAYOFSERVICE   TRIPID  PROGRNUMBER  \
0           0         DB  25-AUG-18 00:00:00  7329034           32   
1           1         DB  31-MAY-18 00:00:00  6847697           13   
2           2         DB  26-MAY-18 00:00:00  6780534           14   
3           3         DB  23-APR-18 00:00:00  6635422            7   
4           4         DB  06-APR-18 00:00:00  6606411           33   

   STOPPOINTID  PLANNEDTIME_ARR  PLANNEDTIME_DEP  ACTUALTIME_ARR  \
0          609            46010            46010           45900   
1          847            33619            33619           33604   
2         4758            57703            57703           57898   
3         7030            27325            27325           27474   
4         1453            85482            85482           86219   

   ACTUALTIME_DEP  ...  NOTE_x  LINEID  ROUTEID  DIRECTION   BASIN  TENDERLOT  \
0           45900  ...     NaN     29A   29A_15          2  BasDef        NaN   
1           33616  ...     NaN     145  145_102          1  BasDef        NaN   
2           57917  ...     NaN      49    49_28          2  BasDef        NaN   
3           27511  ...     NaN     39A   39A_43          2  BasDef        NaN   
4           86219  ...     NaN     123   123_36          2  BasDef        NaN   

   SUPPRESSED_y JUSTIFICATIONID_y        LASTUPDATE_y     NOTE_y  
0           NaN               NaN  03-SEP-18 10:39:32  ,2478282,  
1           NaN               NaN  14-JUN-18 14:04:06  ,3272689,  
2           NaN               NaN  14-JUN-18 13:12:56  ,1726258,  
3           NaN               NaN  13-JUN-18 08:27:05  ,2424410,  
4           NaN               NaN  18-APR-18 10:49:06  ,3222191,  

[5 rows x 28 columns]

In [9]:
df1.drop('Unnamed: 0',axis=1,inplace=True)

# dtypes 
df1['DATASOURCE'] = df1['DATASOURCE'].astype('category')
df1['DAYOFSERVICE'] = df1['DAYOFSERVICE'].astype('datetime64')
df1['TRIPID'] = df1['TRIPID'].astype('object')
df1['PROGRNUMBER'] = df1['PROGRNUMBER'].astype('category')
df1['STOPPOINTID'] = df1['STOPPOINTID'].astype('category')
df1['VEHICLEID'] = df1['VEHICLEID'].astype('object')
df1['SUPPRESSED_x'] = df1['SUPPRESSED_x'].astype('category')
df1['JUSTIFICATIONID_x'] = df1['JUSTIFICATIONID_x'].astype('category')
df1['DIRECTION'] = df1['DIRECTION'].astype('category')
df1['SUPPRESSED_y'] = df1['SUPPRESSED_y'].astype('category')
df1['JUSTIFICATIONID_y'] = df1['JUSTIFICATIONID_y'].astype('category')
df1['TENDERLOT'] = df1['TENDERLOT'].astype('category')
df1['NOTE_x'] = df1['NOTE_x'].astype('category')
df1['PASSENGERS'] = df1['PASSENGERS'].astype('category')
df1['PASSENGERSIN'] = df1['PASSENGERSIN'].astype('category')
df1['PASSENGERSOUT'] = df1['PASSENGERSOUT'].astype('category')
df1['DISTANCE'] = df1['DISTANCE'].astype('category')
df1['NOTE_y'] = df1['DISTANCE'].astype('category')
df1['LASTUPDATE_x'] = df1['LASTUPDATE_x'].astype('datetime64')
df1['LASTUPDATE_y'] = df1['LASTUPDATE_y'].astype('datetime64')
df1['BASIN'] = df1['BASIN'].astype('category')
df1['LINEID'] = df1['LINEID'].astype('category')

categorical_columns = df1.select_dtypes('category').columns
numerical_columns = df1.select_dtypes('int64','float64').columns
object_columns = df1.select_dtypes('object').columns

In [10]:
df1[categorical_columns].describe().T

count unique          top     freq
DATASOURCE         1000000      1           DB  1000000
PROGRNUMBER        1000000    105           13    18239
STOPPOINTID        1000000   4730         1478     1777
PASSENGERS               0      0          NaN      NaN
PASSENGERSIN             0      0          NaN      NaN
PASSENGERSOUT            0      0          NaN      NaN
DISTANCE                 0      0          NaN      NaN
SUPPRESSED_x          4986      2            0     3753
JUSTIFICATIONID_x     4985   3403  4.84981e+17       26
NOTE_x                   0      0          NaN      NaN
LINEID             1000000    130           40    37314
DIRECTION          1000000      2            2   505863
BASIN              1000000      1       BasDef  1000000
TENDERLOT                0      0          NaN      NaN
SUPPRESSED_y           556      1            0      556
JUSTIFICATIONID_y      555    470       291650        6
NOTE_y                   0      0          NaN      NaN

In [11]:
df1.drop(['PASSENGERS','PASSENGERSIN','PASSENGERSOUT','DISTANCE','NOTE_x'],axis=1,inplace=True)
df1.drop(['TENDERLOT','NOTE_y','BASIN','SUPPRESSED_y','JUSTIFICATIONID_y'],axis=1,inplace=True)

categorical_columns = df1.select_dtypes('category').columns

df1.head()


# In[16]:


df1_simple = df1.drop([
    'LASTUPDATE_y',
    'ROUTEID',
    'LASTUPDATE_x',
    'JUSTIFICATIONID_x',
    'SUPPRESSED_x',
    'ACTUALTIME_DEP',
    'VEHICLEID',
    'PLANNEDTIME_DEP'
],axis=1)

# df1_simple['MONTH'] = df1_simple['DAYOFSERVICE'].dt.month.astype('category')
# df1_simple['WEEKDAY'] = df1_simple['DAYOFSERVICE'].dt.weekday.astype('category')
# df1_simple.drop('DAYOFSERVICE',axis=1,inplace=True)

In [12]:
df1_simple.head()

DATASOURCE DAYOFSERVICE   TRIPID PROGRNUMBER STOPPOINTID  PLANNEDTIME_ARR  \
0         DB   2018-08-25  7329034          32         609            46010   
1         DB   2018-05-31  6847697          13         847            33619   
2         DB   2018-05-26  6780534          14        4758            57703   
3         DB   2018-04-23  6635422           7        7030            27325   
4         DB   2018-04-06  6606411          33        1453            85482   

   ACTUALTIME_ARR LINEID DIRECTION  
0           45900    29A         2  
1           33604    145         1  
2           57898     49         2  
3           27474    39A         2  
4           86219    123         2

In [13]:
dftrips = pd.read_csv('../../data/rt_trips_DB_2018.txt',sep=';')

dftrips.head()

DATASOURCE        DAYOFSERVICE   TRIPID LINEID  ROUTEID  DIRECTION  \
0         DB  07-FEB-18 00:00:00  6253783     68    68_80          1   
1         DB  07-FEB-18 00:00:00  6262138    25B  25B_271          2   
2         DB  07-FEB-18 00:00:00  6254942    45A   45A_70          2   
3         DB  07-FEB-18 00:00:00  6259460    25A  25A_273          1   
4         DB  07-FEB-18 00:00:00  6253175     14    14_15          1   

   PLANNEDTIME_ARR  PLANNEDTIME_DEP  ACTUALTIME_ARR  ACTUALTIME_DEP   BASIN  \
0            87245            84600         87524.0         84600.0  BasDef   
1            30517            26460         32752.0             NaN  BasDef   
2            35512            32100         36329.0         32082.0  BasDef   
3            57261            54420         58463.0         54443.0  BasDef   
4            85383            81600         84682.0         81608.0  BasDef   

   TENDERLOT  SUPPRESSED  JUSTIFICATIONID          LASTUPDATE       NOTE  
0        NaN         NaN              NaN  28-FEB-18 12:05:11  ,2967409,  
1        NaN         NaN              NaN  28-FEB-18 12:05:11  ,2580260,  
2        NaN         NaN              NaN  28-FEB-18 12:05:11  ,2448968,  
3        NaN         NaN              NaN  28-FEB-18 12:05:11  ,3094242,  
4        NaN         NaN              NaN  28-FEB-18 12:05:11  ,2526331,

In [14]:
dftrips.drop(['BASIN','TENDERLOT','SUPPRESSED','JUSTIFICATIONID','LASTUPDATE','NOTE','ROUTEID',],axis=1,inplace=True)

In [15]:
dftrips['DAYOFSERVICE'] = dftrips['DAYOFSERVICE'].astype('datetime64')

In [16]:
dftrips.head()

DATASOURCE DAYOFSERVICE   TRIPID LINEID  DIRECTION  PLANNEDTIME_ARR  \
0         DB   2018-02-07  6253783     68          1            87245   
1         DB   2018-02-07  6262138    25B          2            30517   
2         DB   2018-02-07  6254942    45A          2            35512   
3         DB   2018-02-07  6259460    25A          1            57261   
4         DB   2018-02-07  6253175     14          1            85383   

   PLANNEDTIME_DEP  ACTUALTIME_ARR  ACTUALTIME_DEP  
0            84600         87524.0         84600.0  
1            26460         32752.0             NaN  
2            32100         36329.0         32082.0  
3            54420         58463.0         54443.0  
4            81600         84682.0         81608.0

In [17]:
df_merged = df1_simple.merge(dftrips,how='left',on=['DATASOURCE','DAYOFSERVICE','TRIPID'])

In [18]:
df_merged.head()

DATASOURCE DAYOFSERVICE   TRIPID PROGRNUMBER STOPPOINTID  PLANNEDTIME_ARR_x  \
0         DB   2018-08-25  7329034          32         609              46010   
1         DB   2018-05-31  6847697          13         847              33619   
2         DB   2018-05-26  6780534          14        4758              57703   
3         DB   2018-04-23  6635422           7        7030              27325   
4         DB   2018-04-06  6606411          33        1453              85482   

   ACTUALTIME_ARR_x LINEID_x DIRECTION_x LINEID_y  DIRECTION_y  \
0             45900      29A           2      29A            2   
1             33604      145           1      145            1   
2             57898       49           2       49            2   
3             27474      39A           2      39A            2   
4             86219      123           2      123            2   

   PLANNEDTIME_ARR_y  PLANNEDTIME_DEP  ACTUALTIME_ARR_y  ACTUALTIME_DEP  
0              46917            44400           46687.0         44412.0  
1              36580            31800           36935.0         31849.0  
2              59829            56700           60642.0         56811.0  
3              31941            27000           33182.0         26927.0  
4              86085            83400           86860.0         83467.0

In [19]:
df_merged.drop(['LINEID_y','DIRECTION_y'],axis=1,inplace=True)
df_merged.rename(columns={'LINEID_x':'LINEID','DIRECTION_x':'DIRECTION'}, inplace=True)

In [20]:
df_merged['TRIP_FRAC'] = (df_merged['ACTUALTIME_ARR_y'] - df_merged['ACTUALTIME_ARR_x'])/(df_merged['ACTUALTIME_ARR_y'] - df_merged['PLANNEDTIME_DEP'])

In [21]:
stopfractions = df_merged.groupby(['LINEID','DIRECTION','STOPPOINTID'], as_index=False)['TRIP_FRAC'].mean().dropna()

In [22]:
stopfractions.reset_index(drop=True, inplace=True)

In [23]:
stopfractions.head()

LINEID DIRECTION STOPPOINTID  TRIP_FRAC
0      1         1          44   0.758086
1      1         1          45   0.728995
2      1         1          46   0.703364
3      1         1          47   0.681752
4      1         1          48   0.660377

In [24]:
stopfractionname = "stopfractions.pkl"
pickle.dump(stopfractions,open(stopfractionname,'wb'))

In [25]:
dftrips.head()

DATASOURCE DAYOFSERVICE   TRIPID LINEID  DIRECTION  PLANNEDTIME_ARR  \
0         DB   2018-02-07  6253783     68          1            87245   
1         DB   2018-02-07  6262138    25B          2            30517   
2         DB   2018-02-07  6254942    45A          2            35512   
3         DB   2018-02-07  6259460    25A          1            57261   
4         DB   2018-02-07  6253175     14          1            85383   

   PLANNEDTIME_DEP  ACTUALTIME_ARR  ACTUALTIME_DEP  
0            84600         87524.0         84600.0  
1            26460         32752.0             NaN  
2            32100         36329.0         32082.0  
3            54420         58463.0         54443.0  
4            81600         84682.0         81608.0

In [26]:
dftrips.drop(['TRIPID','DATASOURCE'],axis=1,inplace=True)

In [27]:
dftrips.head()

DAYOFSERVICE LINEID  DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  \
0   2018-02-07     68          1            87245            84600   
1   2018-02-07    25B          2            30517            26460   
2   2018-02-07    45A          2            35512            32100   
3   2018-02-07    25A          1            57261            54420   
4   2018-02-07     14          1            85383            81600   

   ACTUALTIME_ARR  ACTUALTIME_DEP  
0         87524.0         84600.0  
1         32752.0             NaN  
2         36329.0         32082.0  
3         58463.0         54443.0  
4         84682.0         81608.0

In [28]:
dftrips.dropna(inplace=True)

In [29]:
dftrips.dtypes

DAYOFSERVICE       datetime64[ns]
LINEID                     object
DIRECTION                   int64
PLANNEDTIME_ARR             int64
PLANNEDTIME_DEP             int64
ACTUALTIME_ARR            float64
ACTUALTIME_DEP            float64
dtype: object

In [30]:
dftrips['DIRECTION'] = dftrips['DIRECTION'].astype('category')
dftrips['LINEID'] = dftrips['LINEID'].astype('category')
dftrips['ACTUALTIME_ARR'] = dftrips['ACTUALTIME_ARR'].astype('int64')
dftrips['ACTUALTIME_DEP'] = dftrips['ACTUALTIME_DEP'].astype('int64')
dftrips['LINEID'] = dftrips['LINEID'].astype('category')

In [31]:
dftrips['TRIPLENGTH'] = dftrips['ACTUALTIME_ARR'] - dftrips['ACTUALTIME_DEP']
dftrips['dt'] = dftrips['DAYOFSERVICE'] + pd.to_timedelta(dftrips['ACTUALTIME_DEP'], unit='s')

In [32]:
dftrips.head()

DAYOFSERVICE LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  \
0   2018-02-07     68         1            87245            84600   
2   2018-02-07    45A         2            35512            32100   
3   2018-02-07    25A         1            57261            54420   
4   2018-02-07     14         1            85383            81600   
5   2018-02-07    77A         2            41648            37200   

   ACTUALTIME_ARR  ACTUALTIME_DEP  TRIPLENGTH                  dt  
0           87524           84600        2924 2018-02-07 23:30:00  
2           36329           32082        4247 2018-02-07 08:54:42  
3           58463           54443        4020 2018-02-07 15:07:23  
4           84682           81608        3074 2018-02-07 22:40:08  
5           42019           37538        4481 2018-02-07 10:25:38

In [33]:
categorical_columns = dftrips.select_dtypes('category').columns
numerical_columns = dftrips.select_dtypes('int64').columns

In [34]:
dftrips.head()

DAYOFSERVICE LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  \
0   2018-02-07     68         1            87245            84600   
2   2018-02-07    45A         2            35512            32100   
3   2018-02-07    25A         1            57261            54420   
4   2018-02-07     14         1            85383            81600   
5   2018-02-07    77A         2            41648            37200   

   ACTUALTIME_ARR  ACTUALTIME_DEP  TRIPLENGTH                  dt  
0           87524           84600        2924 2018-02-07 23:30:00  
2           36329           32082        4247 2018-02-07 08:54:42  
3           58463           54443        4020 2018-02-07 15:07:23  
4           84682           81608        3074 2018-02-07 22:40:08  
5           42019           37538        4481 2018-02-07 10:25:38

In [35]:
dftrips[categorical_columns].describe().T

count unique  top    freq
LINEID     1893367    130  46A   68840
DIRECTION  1893367      2    1  948722

In [36]:
dftrips[numerical_columns].describe().T

count          mean           std      min      25%  \
PLANNEDTIME_ARR  1893367.0  54818.775044  17283.826881  18203.0  39622.0   
PLANNEDTIME_DEP  1893367.0  51298.936625  17434.197250  16200.0  36000.0   
ACTUALTIME_ARR   1893367.0  55188.713192  17279.896452  17546.0  39938.0   
ACTUALTIME_DEP   1893367.0  51334.954109  17439.580453  16187.0  36055.0   
TRIPLENGTH       1893367.0   3853.759083   1434.782157 -14866.0   2803.0   

                     50%      75%      max  
PLANNEDTIME_ARR  54816.0  68651.0  91680.0  
PLANNEDTIME_DEP  51120.0  64800.0  87600.0  
ACTUALTIME_ARR   55224.0  69073.0  94378.0  
ACTUALTIME_DEP   51179.0  64841.0  97177.0  
TRIPLENGTH        3772.0   4845.0  23458.0

In [37]:
dftrips[dftrips['TRIPLENGTH'] < 0].sort_values('ACTUALTIME_ARR',ascending=True)

DAYOFSERVICE LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  \
726144    2018-02-15     41         1            20548            18000   
1917111   2018-10-23     42         2            24331            21600   
1482678   2018-08-25     14         2            24414            23400   
520908    2018-11-08    123         2            26638            23400   
2049497   2018-10-27     11         1            27703            25200   
...              ...    ...       ...              ...              ...   
1051262   2018-10-05    77A         1            82797            79200   
1975479   2018-01-24    150         1            84572            82800   
411291    2018-07-28    111         2            84912            84600   
212027    2018-02-07     13         1            85251            83700   
339290    2018-07-06    120         2            85653            84600   

         ACTUALTIME_ARR  ACTUALTIME_DEP  TRIPLENGTH                  dt  
726144            20186           21595       -1409 2018-02-15 05:59:55  
1917111           24630           25205        -575 2018-10-23 07:00:05  
1482678           24693           26968       -2275 2018-08-25 07:29:28  
520908            27078           28494       -1416 2018-11-08 07:54:54  
2049497           28773           28811         -38 2018-10-27 08:00:11  
...                 ...             ...         ...                 ...  
1051262           84265           97064      -12799 2018-10-06 02:57:44  
1975479           84317           85282        -965 2018-01-24 23:41:22  
411291            84928           86089       -1161 2018-07-28 23:54:49  
212027            85852           88912       -3060 2018-02-08 00:41:52  
339290            85923           86047        -124 2018-07-06 23:54:07  

[103 rows x 9 columns]

In [38]:
dftrips = dftrips[dftrips['TRIPLENGTH'] > 0]

In [39]:
dftrips.drop(['ACTUALTIME_ARR','ACTUALTIME_DEP'],axis=1,inplace=True)

In [40]:
dftrips.head()

DAYOFSERVICE LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  TRIPLENGTH  \
0   2018-02-07     68         1            87245            84600        2924   
2   2018-02-07    45A         2            35512            32100        4247   
3   2018-02-07    25A         1            57261            54420        4020   
4   2018-02-07     14         1            85383            81600        3074   
5   2018-02-07    77A         2            41648            37200        4481   

                   dt  
0 2018-02-07 23:30:00  
2 2018-02-07 08:54:42  
3 2018-02-07 15:07:23  
4 2018-02-07 22:40:08  
5 2018-02-07 10:25:38

In [41]:
dftrips['MONTH'] = dftrips['DAYOFSERVICE'].dt.month.astype('category')
dftrips['WEEKDAY'] = dftrips['DAYOFSERVICE'].dt.weekday.astype('category')
dftrips['WEEKEND'] = dftrips['WEEKDAY'].map(lambda x: x in [5,6]).astype('category')
dftrips['RUSH_HOUR'] = dftrips['PLANNEDTIME_DEP'].map(lambda x : (25200 < x  < 32400) or (57600 < x < 68400)).astype('category')
dftrips.drop(['DAYOFSERVICE'],axis=1,inplace=True)

In [42]:
dftrips[dftrips['WEEKEND'] == True]

LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  TRIPLENGTH  \
38         185         1            58751            57000        1873   
39         185         1            63551            61800        2216   
40         185         1            68351            66600        1937   
41          16         1            37539            33600        4174   
42          16         1            35139            31200        3954   
...        ...       ...              ...              ...         ...   
2178050     11         2            49690            46200        4036   
2178051     11         2            55090            51600        3605   
2178052     11         2            53290            49800        3534   
2178053     11         2            47890            44400        4177   
2178055     76         2            78392            76500        2032   

                         dt MONTH WEEKDAY WEEKEND RUSH_HOUR  
38      2018-02-18 15:49:21     2       6    True     False  
39      2018-02-18 17:13:33     2       6    True      True  
40      2018-02-18 18:29:59     2       6    True      True  
41      2018-02-18 09:21:50     2       6    True     False  
42      2018-02-18 08:40:24     2       6    True      True  
...                     ...   ...     ...     ...       ...  
2178050 2018-05-27 12:50:14     5       6    True     False  
2178051 2018-05-27 14:19:33     5       6    True     False  
2178052 2018-05-27 13:49:54     5       6    True     False  
2178053 2018-05-27 12:22:08     5       6    True     False  
2178055 2018-05-27 21:14:26     5       6    True     False  

[394411 rows x 10 columns]

In [43]:
dftrips.head()

LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  TRIPLENGTH  \
0     68         1            87245            84600        2924   
2    45A         2            35512            32100        4247   
3    25A         1            57261            54420        4020   
4     14         1            85383            81600        3074   
5    77A         2            41648            37200        4481   

                   dt MONTH WEEKDAY WEEKEND RUSH_HOUR  
0 2018-02-07 23:30:00     2       2   False     False  
2 2018-02-07 08:54:42     2       2   False      True  
3 2018-02-07 15:07:23     2       2   False     False  
4 2018-02-07 22:40:08     2       2   False     False  
5 2018-02-07 10:25:38     2       2   False     False

In [44]:
dftrips['PLANNEDTIME_DEP_COS'] = np.cos(2*np.pi*dftrips['PLANNEDTIME_DEP']/(60*60*24))
dftrips['PLANNEDTIME_DEP_SIN'] = np.sin(2*np.pi*dftrips['PLANNEDTIME_DEP']/(60*60*24))

### Add Weather

In [45]:
df_weather = pd.read_csv('../../data/historic_weather_data.csv')

In [46]:
df_weather.head()

dt                         dt_iso  timezone city_name        lat  \
0  1483228800  2017-01-01 00:00:00 +0000 UTC         0    Dublin  53.349805   
1  1483232400  2017-01-01 01:00:00 +0000 UTC         0    Dublin  53.349805   
2  1483236000  2017-01-01 02:00:00 +0000 UTC         0    Dublin  53.349805   
3  1483239600  2017-01-01 03:00:00 +0000 UTC         0    Dublin  53.349805   
4  1483243200  2017-01-01 04:00:00 +0000 UTC         0    Dublin  53.349805   

       lon  temp  feels_like  temp_min  temp_max  ...  wind_deg  rain_1h  \
0 -6.26031  5.89        1.16      5.00      9.17  ...       330      NaN   
1 -6.26031  5.06        0.88      4.80      6.24  ...       310      NaN   
2 -6.26031  5.04        0.85      4.23      6.21  ...       320      NaN   
3 -6.26031  4.59       -1.15      4.00      6.14  ...       330      NaN   
4 -6.26031  4.15       -1.86      3.96      5.89  ...       330      NaN   

   rain_3h  snow_1h  snow_3h  clouds_all  weather_id  weather_main  \
0      NaN      NaN      NaN          75         500          Rain   
1      NaN      NaN      NaN          75         500          Rain   
2      NaN      NaN      NaN          75         803        Clouds   
3      NaN      NaN      NaN          75         803        Clouds   
4      NaN      NaN      NaN          75         803        Clouds   

   weather_description  weather_icon  
0           light rain           10n  
1           light rain           10n  
2        broken clouds           04n  
3        broken clouds           04n  
4        broken clouds           04n  

[5 rows x 25 columns]

In [47]:
df_weather.dtypes

dt                       int64
dt_iso                  object
timezone                 int64
city_name               object
lat                    float64
lon                    float64
temp                   float64
feels_like             float64
temp_min               float64
temp_max               float64
pressure                 int64
sea_level              float64
grnd_level             float64
humidity                 int64
wind_speed             float64
wind_deg                 int64
rain_1h                float64
rain_3h                float64
snow_1h                float64
snow_3h                float64
clouds_all               int64
weather_id               int64
weather_main            object
weather_description     object
weather_icon            object
dtype: object

In [48]:
df_weather.drop([
    'city_name',
    'timezone',
    'weather_icon',
    'weather_description',
    'sea_level',
    'grnd_level',
    'lon',
    'lat',
    'dt_iso',
    'weather_id',
    'rain_1h',
    'rain_3h',
    'snow_1h',
    'snow_3h',
    'clouds_all',
    'temp_min',
    'temp_max',
    'pressure',
    'humidity',
    'wind_speed',
    'wind_deg',
    'temp'
],axis=1,inplace=True)

In [49]:
df_weather.dtypes

dt                int64
feels_like      float64
weather_main     object
dtype: object

In [50]:
df_weather['weather_main'] = df_weather['weather_main'].astype('category')

In [51]:
import datetime

df_weather['dt'] = pd.to_datetime(df_weather['dt'], unit='s')

In [52]:
df_weather.head()

dt  feels_like weather_main
0 2017-01-01 00:00:00        1.16         Rain
1 2017-01-01 01:00:00        0.88         Rain
2 2017-01-01 02:00:00        0.85       Clouds
3 2017-01-01 03:00:00       -1.15       Clouds
4 2017-01-01 04:00:00       -1.86       Clouds

In [53]:
df_weather['month'] = df_weather['dt'].dt.month

In [54]:
avg_monthly_temp = df_weather.groupby('month')['feels_like'].mean()
avg_monthly_weather = df_weather.groupby('month')['weather_main'].agg(lambda x:x.value_counts().index[0])

avg_monthly_weather = pd.DataFrame({'feels_like':avg_monthly_temp,'weather_main':avg_monthly_weather})
avg_monthly_weather.tail()

feels_like weather_main
month                         
8       12.500821       Clouds
9        9.372250       Clouds
10       6.160408       Clouds
11       2.620289       Clouds
12       1.757549       Clouds

In [55]:
wloc = 'avg_monthly_weather.pkl'
pickle.dump(avg_monthly_weather,open(wloc,'wb'))

In [56]:
dftrips = pd.merge_asof(dftrips.sort_values('dt'),df_weather)

In [57]:
dftrips.drop('dt',axis=1,inplace=True)

In [58]:
dftrips.dtypes

LINEID                 category
DIRECTION              category
PLANNEDTIME_ARR           int64
PLANNEDTIME_DEP           int64
TRIPLENGTH                int64
MONTH                  category
WEEKDAY                category
WEEKEND                category
RUSH_HOUR              category
PLANNEDTIME_DEP_COS     float64
PLANNEDTIME_DEP_SIN     float64
feels_like              float64
weather_main           category
month                     int64
dtype: object

In [59]:
print(dftrips.shape)
dfs = dict()
for line in dftrips['LINEID'].unique():
    dfs[line] = dict()
    for direction in dftrips[dftrips['LINEID'] == line]['DIRECTION'].unique():
        dfs[line][direction] = dftrips[dftrips['LINEID'] == line][dftrips['DIRECTION'] == direction].drop(['LINEID','DIRECTION'],axis=1)

(1893264, 14)


C:\Users\Mesel\Anaconda3\lib\site-packages\ipykernel_launcher.py:6: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  


In [60]:
dftrips.head()

LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  TRIPLENGTH MONTH  \
0     66         1            28733            25500        3777     1   
1    77A         1            28947            25800        3260     1   
2     41         2            27785            26100        1473     1   
3     83         1            29314            26400        2758     1   
4    130         2            28305            27000        1044     1   

  WEEKDAY WEEKEND RUSH_HOUR  PLANNEDTIME_DEP_COS  PLANNEDTIME_DEP_SIN  \
0       0   False      True            -0.279829             0.960050   
1       0   False      True            -0.300706             0.953717   
2       0   False      True            -0.321439             0.946930   
3       0   False      True            -0.342020             0.939693   
4       0   False      True            -0.382683             0.923880   

   feels_like weather_main  month  
0        -1.5       Clouds      1  
1        -1.5       Clouds      1  
2        -1.5       Clouds      1  
3        -1.5       Clouds      1  
4        -1.5       Clouds      1

In [61]:
# dftrips.drop(['PLANNEDTIME_DEP_COS','PLANNEDTIME_DEP_SIN'],axis=1,inplace=True)
# dftrips.drop('MONTH',axis=1,inplace=True)
# dftrips.drop('WEEKDAY',axis=1,inplace=True)

In [62]:
dftrips.dtypes

LINEID                 category
DIRECTION              category
PLANNEDTIME_ARR           int64
PLANNEDTIME_DEP           int64
TRIPLENGTH                int64
MONTH                  category
WEEKDAY                category
WEEKEND                category
RUSH_HOUR              category
PLANNEDTIME_DEP_COS     float64
PLANNEDTIME_DEP_SIN     float64
feels_like              float64
weather_main           category
month                     int64
dtype: object

In [63]:
def gen_models(model,dfs,max_iter=200):
    models = dict()
    train_test = dict()
    for route in dfs:
        models[route] = dict()
        train_test[route] = dict()
        for direction in dfs[route]:
            train_test[route][direction] = dict()
            df_rev1 = pd.get_dummies(dfs[route][direction])
        
#             print(route, direction)
            # y is the target
            y = df_rev1["TRIPLENGTH"]
            # X is everything else
            X = df_rev1.drop(["TRIPLENGTH"],1)
            # Split the dataset into two datasets: 70% training and 30% test
            X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1,  test_size=0.3)

#             timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
    #         timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
            
    #         X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    #         X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    #         X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    #         X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
            
    #         print("original range is: ",df_rev1.shape[0])
    #         print("training range (70%):\t rows 0 to", round(X_train.shape[0]))
    #         print("test range (30%): \t rows", round(X_train.shape[0]), "to", round(X_train.shape[0]) + X_test.shape[0])
            
            # need to reset the index to allow contatenation with predicted values otherwise not joining on same index...
            X_train.reset_index(drop=True, inplace=True)
            y_train.reset_index(drop=True, inplace=True)
            X_test.reset_index(drop=True, inplace=True)
            y_test.reset_index(drop=True, inplace=True)
            X_train.head(5)
        
            timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
            timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
            X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
            X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
            X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
            X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
            
            if model == MLPRegressor:
                output_model = model(max_iter=max_iter).fit(X_train, y_train)
            else: 
                output_model = model().fit(X_train, y_train)
            
            models[route][direction] = output_model
            train_test[route][direction] = {
                'X_train':X_train,
                'X_test':X_test,
                'y_train':y_train,
                'y_test':y_test,
                'timetabled_values_train':timetabled_values_train,
                'timetabled_values_test':timetabled_values_test
            }
    return models, train_test

In [64]:
models_LR, train_test_LR = gen_models(LinearRegression,dfs)

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,
C:\Users\Mesel\Anaconda3\lib\site-packages\pan

In [65]:
def mean_absolute_percentage_error(y_true, y_pred): 
#     y_true, y_pred = check_arrays(y_true, y_pred)

    ## Note: does not handle mix 1d representation
    #if _is_1d(y_true): 
    #    y_true, y_pred = _check_1d_array(y_true, y_pred)

    return np.mean(np.abs((y_true - y_pred) / y_true)) * 100


#This function is used repeatedly to compute all metrics
def printMetrics(testActualVal, predictions,timetabled_values):
    #classification evaluation measures
    print('\n==============================================================================')
    print("MAE: ", metrics.mean_absolute_error(testActualVal, predictions))
    #print("MSE: ", metrics.mean_squared_error(testActualVal, predictions))
    print("RMSE: ", metrics.mean_squared_error(testActualVal, predictions)**0.5)
    print("R2: ", metrics.r2_score(testActualVal, predictions))
    print("MAPE: ", mean_absolute_percentage_error(testActualVal, predictions))
    print()
    
    print("MAE: ", metrics.mean_absolute_error(testActualVal, timetabled_values))
    #print("MSE: ", metrics.mean_squared_error(testActualVal, predictions))
    print("RMSE: ", metrics.mean_squared_error(testActualVal, timetabled_values)**0.5)
    print("R2: ", metrics.r2_score(testActualVal, timetabled_values))
    print("MAPE: ", mean_absolute_percentage_error(testActualVal, timetabled_values))


In [66]:
def multiMetrics(models,train_test,train_or_test,printall=False):
    RMSE = 0
    timetable_RMSE = 0
    MAPE = 0
    timetable_MAPE = 0
    count = 0
    badroutes = dict()
    for route in models:
        for direction in models[route]:
            X_train = train_test[route][direction]['X_'+train_or_test]
            y_train = train_test[route][direction]['y_'+train_or_test]
            timetabled_values_train = train_test[route][direction]['timetabled_values_'+train_or_test]
            try:
                predictions_train = models[route][direction].predict(X_train)
        
        #         print(predictions_train/y_train)
        
    
                RMSE += metrics.mean_squared_error(y_train, predictions_train)**0.5
                timetable_RMSE += metrics.mean_squared_error(y_train, timetabled_values_train)**0.5

                MAPE += mean_absolute_percentage_error(y_train, predictions_train)
                timetable_MAPE += mean_absolute_percentage_error(y_train, timetabled_values_train)
        
                count += 1
                if printall == True:
                    print(route, direction)
                    printMetrics(y_train,predictions_train,timetabled_values_train)
                    print("Training set size: ", X_train.size)
                    
                if metrics.mean_squared_error(y_train, predictions_train)**0.5 > metrics.mean_squared_error(y_train, timetabled_values_train)**0.5:
                    badroutes[route + "_" + str(direction)] = {
                        'training_size':X_train.size,
                        'abs_percent_difference': mean_absolute_percentage_error(y_train, predictions_train) - mean_absolute_percentage_error(y_train, timetabled_values_train)
                    }
            except:
                pass
            
    print()
    print('Average model RMSE: ', RMSE/count)
    print('Average timetable RMSE: ', timetable_RMSE/count)
    print()
    print('Average model MAPE: ', MAPE/count)
    print('Average timetable MAPE: ', timetable_MAPE/count)
    print()
    print('Bad routes:' )
    print('---')
    for route in badroutes:
        print(route, '\t', badroutes[route]['training_size'], '\t', badroutes[route]['abs_percent_difference'])
    print()
    print("Total bad routes: %s"%len(badroutes.keys()))

In [67]:
def pool_process(f, data, pool_size):
    import multiprocessing
    from multiprocessing import Pool
    
    print('No. Inputs: %s, pool_size: %s'%(len(data),pool_size))
    tp1 = time.time()
    pool = Pool(processes=pool_size) # initialize the Pool.
    result = pool.map(f, data)       # map f to the data using the Pool of processes to do the work 
    pool.close() # No more processes
    pool.join()  # Wait for the pool processing to complete. 
    return result

## Commented out lengthy code for training various neural networks with multiprocessing

multiMetrics(models_LR,train_test_LR,'train')

multiMetrics(models_LR,train_test_LR,'test')

mkdir -p LR1

mname = 'LR1/models.pkl'
ttname = 'LR1/train_test.pkl'
pickle.dump(models_LR,open(mname,'wb'))
pickle.dump(train_test_LR,open(ttname,'wb'))

models_KNR, train_test_KNR = gen_models(KNeighborsRegressor,dfs)

multiMetrics(models_KNR,train_test_KNR,'train')

multiMetrics(models_KNR,train_test_KNR,'test',printall=True)

mkdir KNR1

mname = 'KNR1/models.pkl'
ttname = 'KNR1/train_test.pkl'
pickle.dump(models_KNR,open(mname,'wb'))
pickle.dump(train_test_KNR,open(ttname,'wb'))

import warnings
warnings.filterwarnings('ignore')

import time
time1 = time.time()

models_NN_200, train_test_NN_200 = gen_models(MLPRegressor,dfs,max_iter=200)
print()
print("Seconds taken: ", time.time()-time1)

multiMetrics(models_NN_200,train_test_NN_200,'train',printall=False)

multiMetrics(models_NN_200,train_test_NN_200,'test',printall=False)

mkdir NN_200

mname = 'NN_200/models.pkl'
ttname = 'NN_200/train_test.pkl'
pickle.dump(models_NN_200,open(mname,'wb'))
pickle.dump(train_test_NN_200,open(ttname,'wb'))

import warnings
warnings.filterwarnings('ignore')

import time
time1 = time.time()

models_NN_500, train_test_NN_500 = gen_models(MLPRegressor,dfs,max_iter=500)
print()
print("Seconds taken: ", time.time()-time1)

multiMetrics(models_NN_500,train_test_NN_500,'train',printall=False)

multiMetrics(models_NN_500,train_test_NN_500,'test',printall=False)

mname = 'NN_500/models.pkl'
ttname = 'NN_500/train_test.pkl'
pickle.dump(models_NN_500,open(mname,'wb'))
pickle.dump(train_test_NN_500,open(ttname,'wb'))

warnings.filterwarnings('ignore')

time1 = time.time()

models_NN_1000, train_test_NN_1000 = gen_models(MLPRegressor,dfs,max_iter=1000)
print()
print("Seconds taken: ", time.time()-time1)

multiMetrics(models_NN_1000,train_test_NN_1000,'train',printall=False)

multiMetrics(models_NN_1000,train_test_NN_1000,'test',printall=False)

mname = 'NN_1000/models.pkl'
ttname = 'NN_1000/train_test.pkl'
pickle.dump(models_NN_1000,open(mname,'wb'))
pickle.dump(train_test_NN_1000,open(ttname,'wb'))

warnings.filterwarnings('ignore')

time1 = time.time()

models_NN_2000, train_test_NN_2000 = gen_models(MLPRegressor,dfs,max_iter=2000)
print()
print("Seconds taken: ", time.time()-time1)

multiMetrics(models_NN_2000,train_test_NN_2000,'train',printall=False)

multiMetrics(models_NN_2000,train_test_NN_2000,'test',printall=False)

mname = 'NN_2000/models.pkl'
ttname = 'NN_2000/train_test.pkl'
pickle.dump(models_NN_2000,open(mname,'wb'))
pickle.dump(train_test_NN_2000,open(ttname,'wb'))

from multiprocessing import Process, Manager

warnings.filterwarnings('ignore')

time1 = time.time()

models_NN_test = pool_process(MLPRegressor,dfs,2)
print()
print("Seconds taken: ", time.time()-time1)

type(models_NN_test)

In [68]:
def gen_NN_mult(key):
    df_rev1 = pd.get_dummies(dfs2[key])
        
#   print(route, direction)
    # y is the target
    y = df_rev1["TRIPLENGTH"]
    # X is everything else
    X = df_rev1.drop(["TRIPLENGTH"],1)
    # Split the dataset into two datasets: 70% training and 30% test
    X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1,  test_size=0.3)

#   timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
#   timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
            
#   X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
#   X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
#   X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
#   X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
            
#   print("original range is: ",df_rev1.shape[0])
#   print("training range (70%):\t rows 0 to", round(X_train.shape[0]))
#   print("test range (30%): \t rows", round(X_train.shape[0]), "to", round(X_train.shape[0]) + X_test.shape[0])
            
# need to reset the index to allow contatenation with predicted values otherwise not joining on same index...
    X_train.reset_index(drop=True, inplace=True)
    y_train.reset_index(drop=True, inplace=True)
    X_test.reset_index(drop=True, inplace=True)
    y_test.reset_index(drop=True, inplace=True)
    X_train.head(5)
        
    timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
    timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
    X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    
    output_model = MLPRegressor(max_iter=2).fit(X_train, y_train)
    test_train_dict[key] = {
                'X_train':X_train,
                'X_test':X_test,
                'y_train':y_train,
                'y_test':y_test,
                'timetabled_values_train':timetabled_values_train,
                'timetabled_values_test':timetabled_values_test
            }
    
    return output_model

In [69]:
dfs2 = dict()
for line in dftrips['LINEID'].unique():
    for direction in dftrips[dftrips['LINEID'] == line]['DIRECTION'].unique():
        dfs2[line+'_'+str(direction)] = dftrips[dftrips['LINEID'] == line][dftrips['DIRECTION'] == direction]

C:\Users\Mesel\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  after removing the cwd from sys.path.


In [70]:
print(dfs2)

{'66_1':         LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  TRIPLENGTH MONTH  \
0           66         1            28733            25500        3777     1   
119         66         1            36533            33300        3160     1   
214         66         1            38933            35700        3388     1   
412         66         1            43044            39300        3200     1   
632         66         1            46644            42900        3240     1   
...        ...       ...              ...              ...         ...   ...   
1892862     66         1            74442            71100        4313    12   
1892965     66         1            76242            72900        3718    12   
1893072     66         1            78042            74700        3929    12   
1893157     66         1            79778            76500        3181    12   
1893229     66         1            81578            78300        3706    12   

        WEEKDAY WEEKEND RUSH_H

In [71]:
import mult_funcs 

test_train_dict = {}
        
# import warnings
# warnings.filterwarnings('ignore')

import time
time1 = time.time()

dfs2 = [item for item in dfs2.values()]
models_NN_test = pool_process(mult_funcs.gen_NN_mult,dfs2,4)
print()
print("Seconds taken: ", time.time()-time1)

No. Inputs: 252, pool_size: 4

Seconds taken:  69.2992742061615


In [72]:
def gen_NN_mult(df):
    df_rev1 = pd.get_dummies(df)
        
#   print(route, direction)
    # y is the target
    y = df_rev1["TRIPLENGTH"]
    # X is everything else
    X = df_rev1.drop(["TRIPLENGTH"],1)
    # Split the dataset into two datasets: 70% training and 30% test
    X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1,  test_size=0.3)

#   timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
#   timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
            
#   X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
#   X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
#   X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
#   X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
            
#   print("original range is: ",df_rev1.shape[0])
#   print("training range (70%):\t rows 0 to", round(X_train.shape[0]))
#   print("test range (30%): \t rows", round(X_train.shape[0]), "to", round(X_train.shape[0]) + X_test.shape[0])
            
# need to reset the index to allow contatenation with predicted values otherwise not joining on same index...
    X_train.reset_index(drop=True, inplace=True)
    y_train.reset_index(drop=True, inplace=True)
    X_test.reset_index(drop=True, inplace=True)
    y_test.reset_index(drop=True, inplace=True)
    X_train.head(5)
        
    timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
    timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
    X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    
    output_model = MLPRegressor(max_iter=2).fit(X_train, y_train)
#     test_train_dict[key] = {
#                 'X_train':X_train,
#                 'X_test':X_test,
#                 'y_train':y_train,
#                 'y_test':y_test,
#                 'timetabled_values_train':timetabled_values_train,
#                 'timetabled_values_test':timetabled_values_test
#             }
    
    return output_model

In [73]:
len(models_NN_test)

252

In [74]:
def unnormalise(x_norm,x_max,x_min):
    return (x_max - x_min)*x_norm + x_min

def multiMetrics_mult(models,train_or_test,printall=False,normalised=True):
    RMSE = 0
    timetable_RMSE = 0
    MAPE = 0
    timetable_MAPE = 0
    count = 0
    badroutes = dict()
    for model in models:
        X = model['X_'+train_or_test]
        y = model['y_'+train_or_test]
        y_max, y_min = model['max_trip'],model['min_trip']
        print(y_max)
        timetabled_values = model['timetabled_values_'+train_or_test]
        try:
            predictions = model['model'].predict(X)
        
        #   print(predictions_train/y_train)
    
            RMSE += metrics.mean_squared_error(y, predictions)**0.5
            timetable_RMSE += metrics.mean_squared_error(y, timetabled_values)**0.5

            MAPE += mean_absolute_percentage_error(y, predictions)
            timetable_MAPE += mean_absolute_percentage_error(y, timetabled_values)
        
            count += 1
            if printall == True:
                print(model['route'], model['direction'])
                if normalised:
                    printMetrics(y,predictions,timetabled_values)
                else:
                    printMetrics(unnormalise(y,y_max,y_min),unnormalise(predictions,y_max,y_min),unnormalise(timetabled_values,y_max,y_min))
                print("Training set size: ", X.size)
                    
            if metrics.mean_squared_error(y, predictions)**0.5 > metrics.mean_squared_error(y, timetabled_values)**0.5:
                badroutes[model['route'] + "_" + str(model['direction'])] = {
                    'training_size':X.size,
                    'mse_difference':metrics.mean_squared_error(y, predictions)**0.5 - metrics.mean_squared_error(y, timetabled_values)**0.5
                }
        except:
            pass
            
    print()
    print('Average model RMSE: ', RMSE/count)
    print('Average timetable RMSE: ', timetable_RMSE/count)
    print()
    print('Average model MAPE: ', MAPE/count)
    print('Average timetable MAPE: ', timetable_MAPE/count)
    print()
    print('Bad routes:' )
    print('---')
    for route in badroutes:
        print(route, '\t', badroutes[route]['training_size'], '\t', badroutes[route]['mse_difference'])
    print()
    print("Total bad routes: %s"%len(badroutes.keys()))

In [75]:
multiMetrics_mult(models_NN_test,'train',printall=True,normalised=False)

9416
66 1

MAE:  339.61525019346465
RMSE:  455.3454164835951
R2:  0.6602941144272516
MAPE:  7.8364376328295435

MAE:  732.8563243465755
RMSE:  846.4072898280665
R2:  -0.17376166927810788
MAPE:  18.44730723668148
Training set size:  273467
8648
66 2

MAE:  344.89415784230596
RMSE:  451.3098521725442
R2:  0.6420554978141032
MAPE:  8.69676035530619

MAE:  424.6658235494145
RMSE:  545.822376300703
R2:  0.4764372510323469
MAPE:  10.866934036565773
Training set size:  234025
13531
77A 1

MAE:  449.76570865500867
RMSE:  601.498321464917
R2:  0.6115578225146103
MAPE:  10.867057839604714

MAE:  567.3955580844803
RMSE:  774.6244525298376
R2:  0.35577148325783114
MAPE:  12.542531103389825
Training set size:  369075
14153
77A 2

MAE:  405.1989431928844
RMSE:  555.6803637624993
R2:  0.6326944188824858
MAPE:  8.578563398244693

MAE:  1037.8772908535962
RMSE:  1172.7129934145805
R2:  -0.6359156269917845
MAPE:  24.261281618078133
Training set size:  403522
13579
41 2

MAE:  389.3812198802098
RMSE:  52

12507
67 1

MAE:  360.09201872460494
RMSE:  472.38149839460016
R2:  0.6007808678872393
MAPE:  8.25214453545165

MAE:  1347.2428890129593
RMSE:  1433.8802504347886
R2:  -2.678335625484913
MAPE:  33.05261111741446
Training set size:  276242
7620
7 2

MAE:  425.1885141602405
RMSE:  555.4829928988883
R2:  0.6695844480753077
MAPE:  10.623987906355167

MAE:  453.41691919819175
RMSE:  601.1927477068301
R2:  0.6129684111833511
MAPE:  11.435244749718205
Training set size:  246309
11861
7 1

MAE:  538.1438365760262
RMSE:  767.3822021383809
R2:  0.41358906841361687
MAPE:  11.802495028965295

MAE:  1051.4736690578666
RMSE:  1241.1020977945977
R2:  -0.5338879375518377
MAPE:  24.244993045706718
Training set size:  216672
9073
29A 2

MAE:  242.59438573121616
RMSE:  331.41923844781735
R2:  0.5698332030419174
MAPE:  9.506249029009432

MAE:  669.4975796995637
RMSE:  736.5961105849098
R2:  -1.1249088157682303
MAPE:  28.974595202855223
Training set size:  394013
6430
29A 1

MAE:  231.8341772649268
RMSE:  

RMSE:  627.6801782719541
R2:  0.49312899473707605
MAPE:  11.6664917452051

MAE:  686.1839414557514
RMSE:  831.8721345473609
R2:  0.10970532812888445
MAPE:  18.92307534768336
Training set size:  209753
13215
14 2

MAE:  527.8880653398843
RMSE:  757.9833853550443
R2:  0.4829383833970804
MAPE:  15.255466996370956

MAE:  493.36664258371223
RMSE:  621.9712004217889
R2:  0.6518523414517496
MAPE:  12.10596945886886
Training set size:  451955
9855
14 1

MAE:  432.68789649533096
RMSE:  584.0738429691296
R2:  0.5399795926467474
MAPE:  9.003327724156632

MAE:  821.3117262350341
RMSE:  947.2525266397031
R2:  -0.2099658925694512
MAPE:  18.294318388374933
Training set size:  438302
9224
25B 2

MAE:  316.35872076335266
RMSE:  436.79370583527344
R2:  0.6392131384191136
MAPE:  8.373942050272671

MAE:  939.0693403778635
RMSE:  1030.3392219438315
R2:  -1.0075133201891462
MAPE:  28.111198753832767
Training set size:  285492
7589
25B 1

MAE:  271.76720630417003
RMSE:  363.89367465468564
R2:  0.619309707877

Training set size:  499241
9400
9 2

MAE:  435.5935411640673
RMSE:  577.892421385788
R2:  0.580719332976712
MAPE:  11.109276391634806

MAE:  504.17096588232977
RMSE:  630.3205161040702
R2:  0.5011916377107479
MAPE:  12.628101863562643
Training set size:  519813
6873
15A 1

MAE:  255.305472760002
RMSE:  341.4679495456707
R2:  0.6815577905706615
MAPE:  10.81620092219196

MAE:  305.13028476652124
RMSE:  408.36538177674436
R2:  0.5445627248714573
MAPE:  11.897116170971781
Training set size:  393828
6871
15A 2

MAE:  300.66193917487067
RMSE:  403.78198588457155
R2:  0.6764337453842036
MAPE:  10.502566633193867

MAE:  562.7925703728379
RMSE:  664.0070591639333
R2:  0.12498653644631563
MAPE:  21.83354164726013
Training set size:  385503
9112
42 1

MAE:  282.64638532214167
RMSE:  386.03141415315906
R2:  0.5572492600476888
MAPE:  8.268388391390118

MAE:  329.2407572819732
RMSE:  443.7964765259939
R2:  0.4148304757686341
MAPE:  9.513933692697421
Training set size:  295297
9326
42 2

MAE:  299.70

33B 2

MAE:  369.98565065871
RMSE:  569.3592750950011
R2:  -0.027074619418949508
MAPE:  19.928464022271136

MAE:  343.04567503418514
RMSE:  545.1274521346083
R2:  0.058489204548199614
MAPE:  16.835659758781492
Training set size:  126910
6204
43 2

MAE:  293.79557835608904
RMSE:  384.96106359103084
R2:  0.5076311734797655
MAPE:  9.931095417470443

MAE:  334.25926970537074
RMSE:  445.9533046586362
R2:  0.33925222328637183
MAPE:  10.84596922192342
Training set size:  191956
6239
43 1

MAE:  298.71322157688974
RMSE:  403.38426654114045
R2:  0.5555851853521235
MAPE:  9.938105484378145

MAE:  331.2323660128003
RMSE:  456.3966867100507
R2:  0.4311004590056753
MAPE:  10.670322715775027
Training set size:  194065
7341
102 2

MAE:  349.2098016283315
RMSE:  475.6355044650798
R2:  0.47573819355991565
MAPE:  12.295703610458213

MAE:  495.9370270793453
RMSE:  585.2795445014523
R2:  0.2061720611237854
MAPE:  17.17562299941666
Training set size:  239020
8493
102 1

MAE:  288.07966310840817
RMSE:  392.

61 1

MAE:  339.4821179081088
RMSE:  464.14661791390876
R2:  0.5494836386231186
MAPE:  11.331280284259494

MAE:  360.30691383980076
RMSE:  531.2768038120291
R2:  0.4097419804000987
MAPE:  11.5960188193082
Training set size:  102934
8867
61 2

MAE:  267.6766253161747
RMSE:  380.4680855761491
R2:  0.7031609215523515
MAPE:  9.054426534575802

MAE:  871.5475437119046
RMSE:  944.2490589407356
R2:  -0.8283432371055983
MAPE:  32.63762882752233
Training set size:  126688
4787
53 2

MAE:  163.74282560305159
RMSE:  245.3260929556423
R2:  0.13625109676290192
MAPE:  12.275490982053434

MAE:  415.35746566454736
RMSE:  453.09558302260876
R2:  -1.9463184220901586
MAPE:  33.77592655153908
Training set size:  105413
7051
53 1

MAE:  546.1699966653266
RMSE:  762.045600877816
R2:  0.24649903654578498
MAPE:  26.159698825226624

MAE:  694.7405270198396
RMSE:  818.5127732734377
R2:  0.1306937268632532
MAPE:  38.55987686227775
Training set size:  105154
8947
185 1

MAE:  376.9819930383177
RMSE:  470.27643035

MAPE:  11.8457554467835
Training set size:  5846
9814
66B 1

MAE:  491.43757827545426
RMSE:  596.2806538966595
R2:  0.388439944236898
MAPE:  14.276371034821493

MAE:  863.3185785863984
RMSE:  1025.1959977962383
R2:  -0.807804560656411
MAPE:  27.244018574546548
Training set size:  119880
7397
66B 2

MAE:  296.40356296306766
RMSE:  411.5414197267166
R2:  0.5881201130906655
MAPE:  8.791386326037829

MAE:  751.5463379208514
RMSE:  834.2086554396941
R2:  -0.6923604409764454
MAPE:  25.330760895989407
Training set size:  110038
7379
38B 2

MAE:  612.1253220583491
RMSE:  727.0044841436774
R2:  0.5428891968207812
MAPE:  15.629823824449668

MAE:  656.4780506233093
RMSE:  776.5471240385597
R2:  0.4784656264193794
MAPE:  17.723072542526054
Training set size:  40071
7128
38B 1

MAE:  454.03815083627893
RMSE:  564.0776425942973
R2:  0.14187072662612377
MAPE:  11.879924721875998

MAE:  951.3683182746731
RMSE:  1079.1633775841465
R2:  -2.1408655163971826
MAPE:  27.169702130223065
Training set size:  2

9033
66X 2

MAE:  476.48586493703635
RMSE:  602.976688283895
R2:  0.27731169778059817
MAPE:  9.030904351296837

MAE:  1011.6253938617474
RMSE:  1133.8513315575328
R2:  -1.5554195297047388
MAPE:  20.39351878642261
Training set size:  46768
8770
66X 1

MAE:  946.6209412616688
RMSE:  1080.7580245575014
R2:  0.07397135057165927
MAPE:  19.305675094176458

MAE:  978.7116739203751
RMSE:  1113.4425820502108
R2:  0.01711402525401995
MAPE:  21.787482682313634
Training set size:  34151
9159
142 1

MAE:  400.107943415876
RMSE:  518.2237135491744
R2:  0.9549272146567978
MAPE:  23.490803417453606

MAE:  497.3966911127353
RMSE:  578.9041319239611
R2:  0.9437538071880487
MAPE:  33.432998409507526
Training set size:  50357
8486
142 2

MAE:  250.76430797322976
RMSE:  349.8798336784528
R2:  0.9774284836592088
MAPE:  12.947930284212363

MAE:  468.0883510500469
RMSE:  546.4119402747349
R2:  0.944949245576946
MAPE:  32.796728940395035
Training set size:  58793
6627
51X 2

MAE:  507.7432259353944
RMSE:  646.

MAPE:  19.017111750850678
Training set size:  2812
4878
116 1

MAE:  635.0142198846024
RMSE:  805.3274175303151
R2:  -0.572092291385953
MAPE:  20.992296604647382

MAE:  848.1475455663647
RMSE:  958.3674179517396
R2:  -1.2263690140935717
MAPE:  28.546671246514745
Training set size:  2849
5660
118 2

MAE:  909.7471660737402
RMSE:  1108.6190212760064
R2:  -2.108484618393486
MAPE:  21.2821643027901

MAE:  699.6306941990575
RMSE:  840.4765715633837
R2:  -0.7866327679258531
MAPE:  18.87448906894966
Training set size:  3552
2442
161 2

MAE:  279.59104023647046
RMSE:  365.0660811217529
R2:  0.11243663964916695
MAPE:  21.47645385385985

MAE:  451.0018401380104
RMSE:  566.5569558503411
R2:  -1.1376842130331455
MAPE:  44.972059322685766
Training set size:  8695
2543
161 1

MAE:  169.03030046246127
RMSE:  222.3632144005902
R2:  0.42499430234963
MAPE:  10.403515961719874

MAE:  359.8100044317111
RMSE:  418.16331417249853
R2:  -1.0334716383230793
MAPE:  24.411758896586306
Training set size:  2331
54

In [76]:
dfs2 = dict()
for line in dftrips['LINEID'].unique():
    for direction in dftrips[dftrips['LINEID'] == line]['DIRECTION'].unique():
        dfs2[line+'_'+str(direction)] = dftrips[dftrips['LINEID'] == line][dftrips['DIRECTION'] == direction]
dfs2_list = [item for item in dfs2.values()]

C:\Users\Mesel\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  after removing the cwd from sys.path.


In [77]:
import mult_funcs 

test_train_dict = {}
        
# import warnings
# warnings.filterwarnings('ignore')

import time
time1 = time.time()


dfs2 = dict()
for line in dftrips['LINEID'].unique():
    for direction in dftrips[dftrips['LINEID'] == line]['DIRECTION'].unique():
        dfs2[line+'_'+str(direction)] = dftrips[dftrips['LINEID'] == line][dftrips['DIRECTION'] == direction]
dfs2_list = [item for item in dfs2.values()]
# models_NN_200_lbfgs = pool_process(mult_funcs.gen_NN_mult_200_lbfgs,dfs2_list,4)
models_NN_200_lbfgs = pool_process(mult_funcs.gen_NN_mult_500,dfs2_list,4)

print()
print("Seconds taken: ", time.time()-time1)

C:\Users\Mesel\Anaconda3\lib\site-packages\ipykernel_launcher.py:15: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  from ipykernel import kernelapp as app


No. Inputs: 252, pool_size: 4

Seconds taken:  83.81998467445374


In [78]:
multiMetrics_mult(models_NN_200_lbfgs,'train')

9416
8648
13531
14153
13579
9445
11430
8640
11027
6252
10181
14277
10201
8344
10188
13978
12552
12222
10323
10792
9422
10415
10804
11737
8858
10319
9224
10271
8395
12507
7620
11861
9073
6430
7195
8675
11668
13502
12888
9779
8660
7728
9270
10253
12335
12957
17375
10031
12815
11879
12138
14325
7332
12041
9912
16262
13215
9855
9224
7589
11321
4854
16040
12770
9314
10935
9600
8681
6160
6253
6356
6379
6540
6543
10651
10236
9189
8450
7647
7392
16011
8616
10385
9652
9464
8442
16083
9400
6873
6871
9112
9326
5144
5286
9768
7828
10100
7625
9548
16871
10955
7503
8865
8613
13861
13655
9911
10014
4817
5815
10267
10002
4145
9748
6204
6239
7341
8493
9444
7604
9662
9083
9752
11463
7071
7557
6589
6952
12644
23458
5444
6689
8546
3517
9862
9864
10278
6612
9995
10226
12122
9885
7596
7970
11008
8867
4787
7051
8947
5755
7007
8411
4552
9007
7893
6457
7816
4398
7846
10881
5880
5266
6825
5296
5550
6068
6216
5647
3726
5810
5916
5158
9814
7397
7379
7128
8830
7979
6499
6659
10569
7786
5691
10783
8848
10488
7237
7

In [79]:
multiMetrics_mult(models_NN_200_lbfgs,'test')

9416
8648
13531
14153
13579
9445
11430
8640
11027
6252
10181
14277
10201
8344
10188
13978
12552
12222
10323
10792
9422
10415
10804
11737
8858
10319
9224
10271
8395
12507
7620
11861
9073
6430
7195
8675
11668
13502
12888
9779
8660
7728
9270
10253
12335
12957
17375
10031
12815
11879
12138
14325
7332
12041
9912
16262
13215
9855
9224
7589
11321
4854
16040
12770
9314
10935
9600
8681
6160
6253
6356
6379
6540
6543
10651
10236
9189
8450
7647
7392
16011
8616
10385
9652
9464
8442
16083
9400
6873
6871
9112
9326
5144
5286
9768
7828
10100
7625
9548
16871
10955
7503
8865
8613
13861
13655
9911
10014
4817
5815
10267
10002
4145
9748
6204
6239
7341
8493
9444
7604
9662
9083

KeyboardInterrupt: 

In [80]:
dfs2_list[0]

LINEID DIRECTION  PLANNEDTIME_ARR  PLANNEDTIME_DEP  TRIPLENGTH MONTH  \
0           66         1            28733            25500        3777     1   
119         66         1            36533            33300        3160     1   
214         66         1            38933            35700        3388     1   
412         66         1            43044            39300        3200     1   
632         66         1            46644            42900        3240     1   
...        ...       ...              ...              ...         ...   ...   
1892862     66         1            74442            71100        4313    12   
1892965     66         1            76242            72900        3718    12   
1893072     66         1            78042            74700        3929    12   
1893157     66         1            79778            76500        3181    12   
1893229     66         1            81578            78300        3706    12   

        WEEKDAY WEEKEND RUSH_HOUR  PLANNEDTIME_DEP_COS  PLANNEDTIME_DEP_SIN  \
0             0   False      True            -0.279829             0.960050   
119           0   False     False            -0.751840             0.659346   
214           0   False     False            -0.854912             0.518773   
412           0   False     False            -0.960050             0.279829   
632           0   False     False            -0.999762             0.021815   
...         ...     ...       ...                  ...                  ...   
1892862       0   False     False             0.442289            -0.896873   
1892965       0   False     False             0.555570            -0.831470   
1893072       0   False     False             0.659346            -0.751840   
1893157       0   False     False             0.751840            -0.659346   
1893229       0   False     False             0.831470            -0.555570   

         feels_like weather_main  month  
0             -1.50       Clouds      1  
119           -2.98       Clouds      1  
214           -2.98       Clouds      1  
412           -3.49       Clouds      1  
632           -4.14       Clouds      1  
...             ...          ...    ...  
1892862        5.78       Clouds     12  
1892965        5.52       Clouds     12  
1893072        5.52       Clouds     12  
1893157        4.87       Clouds     12  
1893229        4.87       Clouds     12  

[10559 rows x 14 columns]

### Tried lgbfs NN with 1000 iters

Performed very well on the training set (8.6% error) with little improvement on test set (12.46% error)

In [81]:
models_NN_200_lbfgs[0]

{'route': '66',
 'direction': 1,
 'model': MLPRegressor(activation='relu', alpha=0.0001, batch_size='auto', beta_1=0.9,
              beta_2=0.999, early_stopping=False, epsilon=1e-08,
              hidden_layer_sizes=(100,), learning_rate='constant',
              learning_rate_init=0.001, max_fun=15000, max_iter=500,
              momentum=0.9, n_iter_no_change=10, nesterovs_momentum=True,
              power_t=0.5, random_state=None, shuffle=True, solver='adam',
              tol=0.0001, validation_fraction=0.1, verbose=False,
              warm_start=False),
 'X_train':       PLANNEDTIME_DEP_COS  PLANNEDTIME_DEP_SIN  feels_like  month  MONTH_1  \
 0               -0.537300             0.843391    0.235018      3        0   
 1                0.831470            -0.555570    0.690464      5        0   
 2               -0.980785             0.195090    0.309536     12        0   
 3               -0.173648             0.984808    0.280875      3        0   
 4               -0.75184

In [82]:
time1 = time.time()

models_SVR_linear = pool_process(mult_funcs.gen_SVR_mult_linear,dfs2_list,4)

print()
print("Seconds taken: ", time.time()-time1)

No. Inputs: 252, pool_size: 4

Seconds taken:  137.75071477890015


In [83]:
multiMetrics_mult(models_SVR_linear,'train',printall=True,normalised=False) 

9416
66 1

MAE:  387.4097507381319
RMSE:  508.6878606331248
R2:  0.5760409795007884
MAPE:  9.02153143658664

MAE:  732.8563243465755
RMSE:  846.4072898280665
R2:  -0.17376166927810788
MAPE:  18.44730723668148
Training set size:  273467
8648
66 2

MAE:  423.75951996345134
RMSE:  544.6429377786008
R2:  0.4786974841386685
MAPE:  10.763207517649032

MAE:  424.6658235494145
RMSE:  545.822376300703
R2:  0.4764372510323469
MAPE:  10.866934036565773
Training set size:  234025
13531
77A 1

MAE:  527.79568042328
RMSE:  673.0688025873471
R2:  0.5136191553683102
MAPE:  12.88640673089721

MAE:  567.3955580844803
RMSE:  774.6244525298376
R2:  0.35577148325783114
MAPE:  12.542531103389825
Training set size:  369075
14153
77A 2

MAE:  515.1750739545249
RMSE:  662.0039389778373
R2:  0.47868697737196764
MAPE:  11.46436649571918

MAE:  1037.8772908535962
RMSE:  1172.7129934145805
R2:  -0.6359156269917845
MAPE:  24.261281618078133
Training set size:  403522
13579
41 2

MAE:  427.2275210081602
RMSE:  558.8

7A 1

MAE:  440.6978554409425
RMSE:  561.1151067956476
R2:  0.5166424941690828
MAPE:  10.498857335880055

MAE:  472.15486059355237
RMSE:  596.5892425769927
R2:  0.4535940994767831
MAPE:  11.556554266830643
Training set size:  224072
10271
7A 2

MAE:  440.9816714761204
RMSE:  568.9749733332502
R2:  0.6644884616680331
MAPE:  10.732686245246551

MAE:  834.0086501888668
RMSE:  967.3068086911208
R2:  0.030272701698946802
MAPE:  22.69892133383607
Training set size:  266844
8395
67 2

MAE:  421.5428488274946
RMSE:  536.5164229598131
R2:  0.38300009963142134
MAPE:  10.642314041807612

MAE:  510.83623173620583
RMSE:  669.3352619949236
R2:  0.03970102924766539
MAPE:  11.625712346109452
Training set size:  233507
12507
67 1

MAE:  424.841511294858
RMSE:  535.2408309038271
R2:  0.48746437221634586
MAPE:  10.083389369382475

MAE:  1347.2428890129593
RMSE:  1433.8802504347886
R2:  -2.678335625484913
MAPE:  33.05261111741446
Training set size:  276242
7620
7 2

MAE:  469.77712153274945
RMSE:  609.124

25A 2

MAE:  386.7113573045323
RMSE:  504.3590079419891
R2:  0.48241389811011137
MAPE:  11.456521619863528

MAE:  355.77511392767485
RMSE:  492.6554746883178
R2:  0.5061561278442104
MAPE:  10.118277445704518
Training set size:  350538
12041
25A 1

MAE:  362.9033391138171
RMSE:  448.159367850475
R2:  0.4713378255235051
MAPE:  11.856452425042189

MAE:  989.0151559002632
RMSE:  1068.2481104512206
R2:  -2.003706862531167
MAPE:  33.204993003270644
Training set size:  343693
9912
18 2

MAE:  472.75286480346546
RMSE:  613.2628826268877
R2:  0.573361131071608
MAPE:  15.123482691831153

MAE:  475.97553975704307
RMSE:  647.122656982154
R2:  0.5249489631892057
MAPE:  13.789429166141016
Training set size:  283383
16262
18 1

MAE:  638.551068460663
RMSE:  786.2812560479506
R2:  0.20461670394962894
MAPE:  17.406591931856894

MAE:  686.1839414557514
RMSE:  831.8721345473609
R2:  0.10970532812888445
MAPE:  18.92307534768336
Training set size:  209753
13215
14 2

MAE:  641.2497592543658
RMSE:  859.1039

17A 2

MAE:  434.73953326253644
RMSE:  560.0067368383567
R2:  0.4707206279342735
MAPE:  11.186453123000502

MAE:  372.8975001522572
RMSE:  517.2365525940592
R2:  0.5484801143737019
MAPE:  8.98607623510849
Training set size:  329781
7392
17A 1

MAE:  413.8911846944766
RMSE:  525.6500904133462
R2:  0.5755241973729459
MAPE:  10.200306706011158

MAE:  443.3891540535902
RMSE:  550.6498721186699
R2:  0.534188145556694
MAPE:  11.519894269032745
Training set size:  364413
16011
37 2

MAE:  497.80705710445443
RMSE:  627.6605424220061
R2:  0.28511864990954106
MAPE:  13.306922710878036

MAE:  925.7369135821523
RMSE:  1022.6559642747518
R2:  -0.8977693262201643
MAPE:  25.42200877924749
Training set size:  214267
8616
37 1

MAE:  426.40220915365205
RMSE:  551.7169224713628
R2:  0.5078615295011508
MAPE:  10.437519131902446

MAE:  775.9163633021718
RMSE:  887.729772845026
R2:  -0.27413743665877965
MAPE:  20.52994188214809
Training set size:  386946
10385
65B 1

MAE:  529.3608940914007
RMSE:  729.2637

140 1

MAE:  461.34497711530634
RMSE:  575.0123850653316
R2:  0.08692549680041883
MAPE:  13.69844888814526

MAE:  601.3441366049954
RMSE:  697.9410406105042
R2:  -0.34520753410888894
MAPE:  18.345481962728336
Training set size:  550116
13655
140 2

MAE:  547.5017926786319
RMSE:  684.4597886707811
R2:  0.25681801360637935
MAPE:  16.365138567023266

MAE:  480.8071101082406
RMSE:  619.0340872070836
R2:  0.39210520460114584
MAPE:  13.121676990573366
Training set size:  494431
9911
47 1

MAE:  496.08592080043434
RMSE:  678.4977674838381
R2:  0.46959601014818064
MAPE:  15.481963324903694

MAE:  432.6863905680069
RMSE:  567.4717498328661
R2:  0.6289790538784585
MAPE:  13.447498198184643
Training set size:  143893
10014
47 2

MAE:  560.9783675705419
RMSE:  712.6900175745849
R2:  0.43816244698446805
MAPE:  15.297429366658896

MAE:  651.4627328125367
RMSE:  820.2565928866035
R2:  0.25576708798543735
MAPE:  18.40985459231974
Training set size:  89244
4817
32 2

MAE:  244.48447201350984
RMSE:  320

120 2

MAE:  280.49299062667967
RMSE:  402.8011904481424
R2:  0.34891584187985514
MAPE:  17.09336187632311

MAE:  399.1219867460472
RMSE:  445.45089224023815
R2:  0.20373925858269282
MAPE:  28.001483065768472
Training set size:  406112
6689
120 1

MAE:  319.9348144812737
RMSE:  437.66042434629674
R2:  0.31469395155642776
MAPE:  18.048561185588376

MAE:  319.6150270175637
RMSE:  376.1795802643935
R2:  0.49370872202520544
MAPE:  20.424503885384667
Training set size:  400821
8546
59 1

MAE:  274.9235701613934
RMSE:  352.68335235704626
R2:  -0.9307513475891176
MAPE:  25.45027923126944

MAE:  370.42566820584426
RMSE:  420.97400716377405
R2:  -1.7508505024150218
MAPE:  33.49158257837602
Training set size:  109372
3517
59 2

MAE:  160.00562690732457
RMSE:  207.1898384565813
R2:  0.31224006679877825
MAPE:  14.03888301509105

MAE:  325.6302540337383
RMSE:  357.62351343063415
R2:  -1.0490478440749844
MAPE:  30.199320306620386
Training set size:  109816
9862
70 2

MAE:  565.0614333253459
RMSE:  7

26 1

MAE:  264.44329510238396
RMSE:  349.6005614375317
R2:  0.41657521646899287
MAPE:  12.745333009192466

MAE:  510.7312301885655
RMSE:  573.4332733467912
R2:  -0.5696629568573282
MAPE:  26.718072215693965
Training set size:  176897
6068
26 2

MAE:  348.6194972423953
RMSE:  501.6818995591374
R2:  0.22080753682759813
MAPE:  17.312877067265152

MAE:  355.8165873212479
RMSE:  470.69519131203407
R2:  0.3140895779119788
MAPE:  18.518154749448485
Training set size:  162652
6216
40B 1

MAE:  340.35653198980094
RMSE:  421.57044998300535
R2:  0.6640829681048406
MAPE:  18.058400798324186

MAE:  371.159645964303
RMSE:  506.3643887638661
R2:  0.5153613879412096
MAPE:  15.544202357601176
Training set size:  47471
5647
40B 2

MAE:  292.84858681412425
RMSE:  420.0533180496842
R2:  0.284293612066987
MAPE:  10.593184480799799

MAE:  788.1324595263234
RMSE:  854.5378591437596
R2:  -1.9620246669399197
MAPE:  30.998385074345048
Training set size:  35076
3726
16C 2

MAE:  169.82356339901196
RMSE:  235.08

9957
67X 1

MAE:  974.189577048368
RMSE:  1167.4287015070133
R2:  0.217176654677536
MAPE:  20.308120828612093

MAE:  989.3305212413376
RMSE:  1139.5016503922407
R2:  0.2541818413156549
MAPE:  21.259620669413735
Training set size:  34447
3075
236 1

MAE:  136.8542109900807
RMSE:  189.09722889276514
R2:  0.44703423573651946
MAPE:  6.665986150578145

MAE:  303.08576954129825
RMSE:  371.31424421444405
R2:  -1.1321174967920435
MAPE:  15.972993289804007
Training set size:  16021
4426
236 2

MAE:  212.94498047400015
RMSE:  319.9610082474956
R2:  0.3112926320047885
MAPE:  9.630371273446107

MAE:  553.9375488773767
RMSE:  631.0412610128476
R2:  -1.6788977006826187
MAPE:  28.173643025639638
Training set size:  11951
6408
39X 2

MAE:  268.45908830759436
RMSE:  352.63644250222086
R2:  0.5485820035843276
MAPE:  6.487056886176649

MAE:  771.1629221058629
RMSE:  858.92667677593
R2:  -1.678160919989896
MAPE:  19.885973056760776
Training set size:  22866
9681
39X 1

MAE:  375.1099173634082
RMSE:  535.0

27X 1

MAE:  303.63605378994987
RMSE:  383.0862412354183
R2:  0.3325332702129461
MAPE:  7.1733970819145165

MAE:  1029.662392843332
RMSE:  1168.2688099670836
R2:  -5.207576476550525
MAPE:  25.48392255594068
Training set size:  10952
4836
38D 1

MAE:  255.75070672447646
RMSE:  340.7430054173902
R2:  0.2234471674647711
MAPE:  7.35041053658739

MAE:  358.2234980073689
RMSE:  446.87708870497187
R2:  -0.3356519021106541
MAPE:  10.768267640611686
Training set size:  6105
4057
38D 2

MAE:  124.33755335932223
RMSE:  149.67988513327705
R2:  0.5550274669932092
MAPE:  3.807841315810979

MAE:  468.2361518811482
RMSE:  540.7319702084203
R2:  -4.807248581936918
MAPE:  14.658403846051959
Training set size:  1628
6170
46E 2

MAE:  346.485627035089
RMSE:  433.1893305353627
R2:  0.459406836404488
MAPE:  8.972204209901177

MAE:  680.8156487081333
RMSE:  788.5433701873685
R2:  -0.7912912967641499
MAPE:  19.162810128842636
Training set size:  9509
8099
41X 2

MAE:  519.1798794455033
RMSE:  647.997225663588

In [84]:
multiMetrics_mult(models_SVR_linear,'test')

9416
8648
13531
14153
13579
9445
11430
8640
11027
6252
10181
14277
10201
8344
10188
13978
12552
12222
10323
10792
9422
10415
10804
11737
8858
10319
9224
10271
8395
12507
7620
11861
9073
6430
7195
8675
11668
13502
12888
9779
8660
7728
9270
10253
12335
12957
17375
10031
12815
11879
12138
14325
7332
12041
9912
16262
13215
9855
9224
7589
11321
4854
16040
12770
9314
10935
9600
8681
6160
6253
6356
6379
6540
6543
10651
10236
9189
8450
7647
7392
16011
8616
10385
9652
9464
8442
16083
9400
6873
6871
9112
9326
5144
5286
9768
7828
10100
7625
9548
16871
10955
7503
8865
8613
13861
13655
9911
10014
4817
5815
10267
10002
4145
9748
6204
6239
7341
8493
9444
7604
9662
9083
9752
11463
7071
7557
6589
6952
12644
23458
5444
6689
8546
3517
9862
9864
10278
6612
9995
10226
12122
9885
7596
7970
11008
8867
4787
7051
8947
5755
7007
8411
4552
9007
7893
6457
7816
4398
7846
10881
5880
5266
6825
5296
5550
6068
6216
5647
3726
5810
5916
5158
9814
7397
7379
7128
8830
7979
6499
6659
10569
7786
5691
10783
8848
10488
7237
7

In [85]:
time1 = time.time()

models_SVR = pool_process(mult_funcs.gen_SVR_mult,dfs2_list,4)

print()
print("Seconds taken: ", time.time()-time1)

No. Inputs: 252, pool_size: 4

Seconds taken:  43.09974670410156


In [86]:
multiMetrics_mult(models_SVR,'train',printall=True) 

9416
66 1

MAE:  0.046927596892059595
RMSE:  0.062011346740815335
R2:  0.6344629770634636
MAPE:  inf

MAE:  0.09621324988139365
RMSE:  0.1111208205104459
R2:  -0.17376166927810766
MAPE:  inf
Training set size:  273467
8648
66 2

MAE:  0.04914377397592096
RMSE:  0.06250402198754564
R2:  0.5985197590356388
MAPE:  inf

MAE:  0.055533650261463896
RMSE:  0.07137732134179457
R2:  0.4764372510323468
MAPE:  inf
Training set size:  234025
13531
77A 1

MAE:  0.03783440690786794
RMSE:  0.0481604330009707
R2:  0.5519874751406023
MAPE:  inf

MAE:  0.042301912926599586
RMSE:  0.057751767131129325
R2:  0.35577148325783114
MAPE:  inf
Training set size:  369075
14153
77A 2

MAE:  0.038121270577402985
RMSE:  0.04899816883718085
R2:  0.5696211843676627
MAPE:  inf

MAE:  0.08454523385904171
RMSE:  0.0955289176779554
R2:  -0.6359156269917845
MAPE:  inf
Training set size:  403522
13579
41 2

MAE:  0.03473569935308971
RMSE:  0.04482755412482245
R2:  0.3218464774038363
MAPE:  inf

MAE:  0.0683859779237865
RMS

7A 2

MAE:  0.047571871849234885
RMSE:  0.06148705994527342
R2:  0.7218824430082491
MAPE:  inf

MAE:  0.09899212465149752
RMSE:  0.11481386453307071
R2:  0.030272701698946913
MAPE:  inf
Training set size:  266844
8395
67 2

MAE:  0.04835018466708618
RMSE:  0.06064166076647557
R2:  0.4534393569614783
MAPE:  10.611940158316216

MAE:  0.061346971506689774
RMSE:  0.0803813212435359
R2:  0.039701029247665276
MAPE:  11.964382436894292
Training set size:  233507
12507
67 1

MAE:  0.041327583635189936
RMSE:  0.05152536509434098
R2:  0.51959818104584
MAPE:  inf

MAE:  0.13396071283811864
RMSE:  0.14257534557370874
R2:  -2.678335625484913
MAPE:  inf
Training set size:  276242
7620
7 2

MAE:  0.06187433303981239
RMSE:  0.07905190240521416
R2:  0.6688141280144061
MAPE:  13.194001401728231

MAE:  0.0644515876614345
RMSE:  0.08545739128739589
R2:  0.6129684111833512
MAPE:  13.708928509804426
Training set size:  246309
11861
7 1

MAE:  0.05789136385617165
RMSE:  0.08166019500288918
R2:  0.39310267579

14 2

MAE:  0.04728658956256147
RMSE:  0.06364462270421137
R2:  0.43812487256023813
MAPE:  26.982084527025556

MAE:  0.03973956041753623
RMSE:  0.05009836491516624
R2:  0.6518523414517496
MAPE:  18.479557955474217
Training set size:  451955
9855
14 1

MAE:  0.05651306699308475
RMSE:  0.07576229956615156
R2:  0.5128947748378825
MAPE:  16.563538972819238

MAE:  0.10353103822450951
RMSE:  0.11940659607206644
R2:  -0.2099658925694512
MAPE:  33.64143104889478
Training set size:  438302
9224
25B 2

MAE:  0.04892098089251309
RMSE:  0.06339485067910862
R2:  0.5842811261447898
MAPE:  inf

MAE:  0.12696989458867813
RMSE:  0.13931033287504482
R2:  -1.007513320189147
MAPE:  inf
Training set size:  285492
7589
25B 1

MAE:  0.04168732331278955
RMSE:  0.053900035048788306
R2:  0.581925409971048
MAPE:  inf

MAE:  0.045741490399024635
RMSE:  0.061150814881196724
R2:  0.4618787097697147
MAPE:  inf
Training set size:  323898
11321
27A 1

MAE:  0.0439699986837123
RMSE:  0.05098059484009718
R2:  -0.5535038

R2:  0.44054626940886565
MAPE:  inf

MAE:  0.0962609467812245
RMSE:  0.11348564916885438
R2:  -0.37178920691153783
MAPE:  inf
Training set size:  208495
8442
54A 1

MAE:  0.044183982778410125
RMSE:  0.057656172667045154
R2:  0.4201214459113327
MAPE:  12.624625765171524

MAE:  0.04328514839257049
RMSE:  0.061555728633191545
R2:  0.33902903726330846
MAPE:  11.268897424037387
Training set size:  231990
16083
9 1

MAE:  0.035337489888029094
RMSE:  0.04383946043458783
R2:  0.4484022028615974
MAPE:  inf

MAE:  0.036011251269712885
RMSE:  0.04435833564839894
R2:  0.43526772596952834
MAPE:  inf
Training set size:  499241
9400
9 2

MAE:  0.052644052311020255
RMSE:  0.06892067844387328
R2:  0.5823071289509556
MAPE:  inf

MAE:  0.060242677247261296
RMSE:  0.07531610898602821
R2:  0.5011916377107479
MAPE:  inf
Training set size:  519813
6873
15A 1

MAE:  0.04177884795023672
RMSE:  0.05355698936306066
R2:  0.6361731327940272
MAPE:  inf

MAE:  0.04477333598921809
RMSE:  0.05992155271852448
R2:  0.54

MAE:  0.059631404517682285
RMSE:  0.07575438951165539
R2:  0.7575304551575185
MAPE:  34.35868157414112
Training set size:  144411
4145
33B 1

MAE:  0.05556361911362027
RMSE:  0.07527692730930033
R2:  0.1612587719543207
MAPE:  inf

MAE:  0.05139945543070669
RMSE:  0.06861501891298455
R2:  0.303144713824803
MAPE:  inf
Training set size:  170422
9748
33B 2

MAE:  0.04053802803970322
RMSE:  0.06212019822453435
R2:  -0.06405738301478281
MAPE:  32.73075616271785

MAE:  0.03677196645237272
RMSE:  0.058433642634216784
R2:  0.0584892045481995
MAPE:  24.873022247817374
Training set size:  126910
6204
43 2

MAE:  0.04955888736022408
RMSE:  0.0630237318845667
R2:  0.49222802036760926
MAPE:  10.819413779695374

MAE:  0.05388671122124306
RMSE:  0.0718931653488048
R2:  0.33925222328637183
MAPE:  10.849663003690198
Training set size:  191956
6239
43 1

MAE:  0.0554215827457197
RMSE:  0.07068171491143194
R2:  0.5092810027191839
MAPE:  inf

MAE:  0.05523301084088716
RMSE:  0.07610416653494258
R2:  0.431

84 2

MAE:  0.06310110354145787
RMSE:  0.08486734227530254
R2:  0.5715073147057841
MAPE:  inf

MAE:  0.072588383202974
RMSE:  0.09092251159426337
R2:  0.5081812784053097
MAPE:  inf
Training set size:  135679
12122
69 1

MAE:  0.046004492167196084
RMSE:  0.05477854288244561
R2:  0.0329934166166056
MAPE:  inf

MAE:  0.033180472336924
RMSE:  0.04918840371380947
R2:  0.22028850497212316
MAPE:  inf
Training set size:  138713
9885
69 2

MAE:  0.04712849937846356
RMSE:  0.06370215597469524
R2:  0.656111759210932
MAPE:  inf

MAE:  0.08078476955486646
RMSE:  0.09589209476973988
R2:  0.22075383238694235
MAPE:  inf
Training set size:  132904
7596
17 2

MAE:  0.0696921517771861
RMSE:  0.09161148862085887
R2:  0.6218997937683786
MAPE:  inf

MAE:  0.11067577629869751
RMSE:  0.13230613839773492
R2:  0.21138138942640983
MAPE:  inf
Training set size:  208051
7970
17 1

MAE:  0.06632574976502122
RMSE:  0.0963853468906837
R2:  0.46073729530674756
MAPE:  33.349985496597846

MAE:  0.057795765595421246
RMSE

MAPE:  inf

MAE:  0.061277801876226355
RMSE:  0.0835998660663474
R2:  0.5153613879412096
MAPE:  inf
Training set size:  47471
5647
40B 2

MAE:  0.07008008928714128
RMSE:  0.10220847196096317
R2:  0.36142647714565856
MAPE:  44.8119865308233

MAE:  0.2030222719027108
RMSE:  0.22012824810503853
R2:  -1.9620246669399188
MAPE:  142.78493948155793
Training set size:  35076
3726
16C 2

MAE:  0.07242199691248923
RMSE:  0.09989049477249115
R2:  0.6602599584873161
MAPE:  inf

MAE:  0.21624435546307097
RMSE:  0.24448142795774705
R2:  -1.0351206172254037
MAPE:  inf
Training set size:  7289
5810
16C 1

MAE:  0.03871037991473055
RMSE:  0.054156293537562815
R2:  0.25577594755583344
MAPE:  inf

MAE:  0.09608472685256203
RMSE:  0.10580027803921277
R2:  -1.8403996649700272
MAPE:  inf
Training set size:  27787
5916
7D 2

MAE:  0.10157635958643597
RMSE:  0.1248972664084998
R2:  0.6840907929590674
MAPE:  inf

MAE:  0.16852015672780343
RMSE:  0.1968819930374779
R2:  0.2150022513717168
MAPE:  inf
Training se

R2:  0.5010459691358695
MAPE:  inf

MAE:  0.13231889648199568
RMSE:  0.1466099770133268
R2:  -1.0275752094359865
MAPE:  inf
Training set size:  107337
8273
114 2

MAE:  0.044829194460376885
RMSE:  0.05546352342561663
R2:  0.1888571257316738
MAPE:  inf

MAE:  0.08151285500269147
RMSE:  0.09052964276079357
R2:  -1.161046239761431
MAPE:  inf
Training set size:  106190
4707
70D 2

MAE:  0.11814109599350908
RMSE:  0.14883914523042302
R2:  0.4500690991132983
MAPE:  43.87112451798122

MAE:  0.32138334332080865
RMSE:  0.35877750202425274
R2:  -2.195392361330401
MAPE:  141.7151754000579
Training set size:  3515
6132
70D 1

MAE:  0.10612913424793179
RMSE:  0.14326097345422636
R2:  0.16194023563906768
MAPE:  inf

MAE:  0.3213513198884634
RMSE:  0.3465965729887775
R2:  -3.905324284560259
MAPE:  inf
Training set size:  4292
6719
32X 1

MAE:  0.12468436721506201
RMSE:  0.15568587324006355
R2:  0.45376517498831304
MAPE:  49.67467752266443

MAE:  0.33505652500459404
RMSE:  0.3735186305971611
R2:  -2.1

31D 2

MAE:  0.11754648385806099
RMSE:  0.15119178490060656
R2:  0.3394980266995631
MAPE:  inf

MAE:  0.2568781343947589
RMSE:  0.2957813635504911
R2:  -1.5278968257338965
MAPE:  inf
Training set size:  4477
4000
31D 1

MAE:  0.0898741688646019
RMSE:  0.11975661665063911
R2:  0.21325034603789628
MAPE:  inf

MAE:  0.2678806166461666
RMSE:  0.3000265844785094
R2:  -3.9380672573015314
MAPE:  inf
Training set size:  4625
6807
25D 2

MAE:  0.09862481450243075
RMSE:  0.12585447301369246
R2:  0.24623093251857986
MAPE:  inf

MAE:  0.197328277336944
RMSE:  0.22404971035086638
R2:  -1.3888549141414397
MAPE:  inf
Training set size:  14208
6962
25D 1

MAE:  0.06159734588688392
RMSE:  0.08837354642678559
R2:  0.1676858447503521
MAPE:  31.91755492079124

MAE:  0.20039690618092446
RMSE:  0.21670450997909835
R2:  -4.004706497802663
MAPE:  105.3182309107126
Training set size:  18981
6312
15D 2

MAE:  0.11503240052953038
RMSE:  0.15484263348918414
R2:  0.42123671613039826
MAPE:  inf

MAE:  0.20716716533

In [87]:
multiMetrics_mult(models_SVR,'test',printall=True) 

9416
66 1

MAE:  0.048962303771973886
RMSE:  0.0645444916108342
R2:  0.6135411315612829
MAPE:  15.757329980607098

MAE:  0.09790810558239944
RMSE:  0.11274856703018793
R2:  -0.1792529491095709
MAPE:  35.73951947314073
Training set size:  117216
8648
66 2

MAE:  0.05039072614484949
RMSE:  0.06417263714673527
R2:  0.5538902895442024
MAPE:  13.77180731079676

MAE:  0.05435277724987438
RMSE:  0.06919509929100827
R2:  0.48132827103653375
MAPE:  14.874871736128693
Training set size:  100344
13531
77A 1

MAE:  0.03766716217709934
RMSE:  0.047233273910417525
R2:  0.569585953702086
MAPE:  11.58131065919333

MAE:  0.04264095477755587
RMSE:  0.0578567514712681
R2:  0.3541994238185312
MAPE:  11.866261310805818
Training set size:  158175
14153
77A 2

MAE:  0.037670992542115984
RMSE:  0.04816467437069549
R2:  0.5748869458677998
MAPE:  19.80614610236214

MAE:  0.08446545961709591
RMSE:  0.09519766455602581
R2:  -0.6607328359148186
MAPE:  47.232160962931424
Training set size:  172938
13579
41 2

MAE: 

7A 2

MAE:  0.04906419331406348
RMSE:  0.06202798741574732
R2:  0.7198603331059648
MAPE:  25.366164954762638

MAE:  0.09757512776573615
RMSE:  0.11394847102507541
R2:  0.05459861985700265
MAPE:  63.367908206546964
Training set size:  114367
8395
67 2

MAE:  0.04876451964543224
RMSE:  0.06167134730824121
R2:  0.45659467930362263
MAPE:  inf

MAE:  0.061646088383268516
RMSE:  0.081038720754645
R2:  0.06169902566357954
MAPE:  inf
Training set size:  100085
12507
67 1

MAE:  0.042313585323927455
RMSE:  0.05431053770108448
R2:  0.4802770005561958
MAPE:  29.130435840895913

MAE:  0.13433113800112048
RMSE:  0.1429961048375295
R2:  -2.602899486070359
MAPE:  93.7141810007864
Training set size:  118400
7620
7 2

MAE:  0.06062522859599858
RMSE:  0.07944752389207024
R2:  0.6653925620122378
MAPE:  inf

MAE:  0.06396179766808306
RMSE:  0.08517656827690956
R2:  0.6153948146163548
MAPE:  inf
Training set size:  105561
11861
7 1

MAE:  0.05726701124290368
RMSE:  0.0806121820614559
R2:  0.387162056001101

MAPE:  inf

MAE:  0.09546212963641117
RMSE:  0.10335602188285883
R2:  -1.8218581877243718
MAPE:  inf
Training set size:  147334
9912
18 2

MAE:  0.04504216740042951
RMSE:  0.05856731812650302
R2:  0.6118629241648952
MAPE:  11.754137455834256

MAE:  0.04898792371947081
RMSE:  0.06600027025961622
R2:  0.5070919825359147
MAPE:  11.57841335922169
Training set size:  121471
16262
18 1

MAE:  0.03987208838623616
RMSE:  0.04805295218274603
R2:  0.25397236591974603
MAPE:  inf

MAE:  0.04415445276774851
RMSE:  0.05280786458781636
R2:  0.09902658042908274
MAPE:  inf
Training set size:  89910
13215
14 2

MAE:  0.047740638426739014
RMSE:  0.06580621191904029
R2:  0.4194949800060538
MAPE:  inf

MAE:  0.03933399933762836
RMSE:  0.04999750822793751
R2:  0.6649042518307324
MAPE:  inf
Training set size:  193695
9855
14 1

MAE:  0.05702012047780748
RMSE:  0.07693682201666624
R2:  0.5010719186360725
MAPE:  inf

MAE:  0.10313343043405082
RMSE:  0.11985742495222712
R2:  -0.21087509753830425
MAPE:  inf
Trai

37 1

MAE:  0.0577252935920197
RMSE:  0.0747550919261321
R2:  0.5838937006550287
MAPE:  20.29755051623812

MAE:  0.11674029290231777
RMSE:  0.13303691463162587
R2:  -0.317853272282526
MAPE:  46.29550712938631
Training set size:  165834
10385
65B 1

MAE:  0.057017601278010026
RMSE:  0.0793341902888237
R2:  0.43036548441697386
MAPE:  19.270330480413847

MAE:  0.050545968295974915
RMSE:  0.07806270413492916
R2:  0.4484781889904369
MAPE:  16.698259087884548
Training set size:  67599
9652
65B 2

MAE:  0.10402834855400155
RMSE:  0.13275283085140824
R2:  0.3100966444829327
MAPE:  47.294032568326976

MAE:  0.10997505362152137
RMSE:  0.14023504264284542
R2:  0.23013641566802656
MAPE:  61.416392120251174
Training set size:  58904
9464
54A 2

MAE:  0.054307464803211046
RMSE:  0.07218722361504844
R2:  0.4298346907366294
MAPE:  26.00549993009321

MAE:  0.09702241812563625
RMSE:  0.11361044935063935
R2:  -0.41226653243703826
MAPE:  53.185962111031614
Training set size:  89355
8442
54A 1

MAE:  0.044

MAPE:  inf

MAE:  0.15928919830091615
RMSE:  0.18035245727250765
R2:  -0.7225498747454191
MAPE:  inf
Training set size:  77330
5815
32 1

MAE:  0.05158003774626048
RMSE:  0.06699068901860997
R2:  0.5946124615898328
MAPE:  11.492898641515053

MAE:  0.059556801715930405
RMSE:  0.07581036786517709
R2:  0.4808430012340018
MAPE:  13.81193535648903
Training set size:  77256
10267
44 1

MAE:  0.052021262550504245
RMSE:  0.06874365207688635
R2:  0.6388724665604492
MAPE:  12.204666614800637

MAE:  0.07170952062752523
RMSE:  0.08899980289101493
R2:  0.39469607546183494
MAPE:  18.58421622515658
Training set size:  59829
10002
44 2

MAE:  0.06570696454799185
RMSE:  0.08614970307676477
R2:  0.6632246764469525
MAPE:  inf

MAE:  0.059316079886476115
RMSE:  0.07746619178551607
R2:  0.7276940659226698
MAPE:  inf
Training set size:  61938
4145
33B 1

MAE:  0.05735272594460322
RMSE:  0.07764930849120533
R2:  0.1290321815300115
MAPE:  32.92328949597512

MAE:  0.05275940495668186
RMSE:  0.06992549981337562

MAE:  0.13179533689001444
RMSE:  0.15230245621705563
R2:  -0.7116309965997307
MAPE:  73.2642888581931
Training set size:  70448
10278
184 1

MAE:  0.04134708086062325
RMSE:  0.04851031302500023
R2:  -0.548358890952731
MAPE:  20.495965358533162

MAE:  0.03230390429576584
RMSE:  0.039119040710597644
R2:  -0.0068849996226727495
MAPE:  16.06673449684881
Training set size:  82140
6612
184 2

MAE:  0.08481851910663461
RMSE:  0.1084321693275018
R2:  0.305606534397288
MAPE:  inf

MAE:  0.14920935252074727
RMSE:  0.161343766205923
R2:  -0.5374242008842822
MAPE:  inf
Training set size:  79217
9995
84 1

MAE:  0.06519197744330686
RMSE:  0.09491852657117372
R2:  0.1997420396528411
MAPE:  30.39694902711052

MAE:  0.06257272026298506
RMSE:  0.07753759590571739
R2:  0.46598594260901294
MAPE:  23.35624759794949
Training set size:  59089
10226
84 2

MAE:  0.06455354880662892
RMSE:  0.0849370310516891
R2:  0.5602261718237386
MAPE:  40.04821910452938

MAE:  0.07012546666204987
RMSE:  0.08667519746867655


26 2

MAE:  0.060969363424421566
RMSE:  0.08806972561396517
R2:  0.29497704160355986
MAPE:  inf

MAE:  0.06717968941103582
RMSE:  0.08704155958620267
R2:  0.3113424692550284
MAPE:  inf
Training set size:  69745
6216
40B 1

MAE:  0.05526164206080295
RMSE:  0.06886119704853438
R2:  0.6577452358055655
MAPE:  18.646929440356367

MAE:  0.06189049603239796
RMSE:  0.08485264186249679
R2:  0.4803258633149248
MAPE:  15.517094484721364
Training set size:  20350
5647
40B 2

MAE:  0.06801241761135628
RMSE:  0.10049967232553016
R2:  0.3276900695441908
MAPE:  inf

MAE:  0.20712327630596664
RMSE:  0.22142653207685828
R2:  -2.263619739156588
MAPE:  inf
Training set size:  15059
3726
16C 2

MAE:  0.08111145847370292
RMSE:  0.10245981096999117
R2:  0.5984672142745273
MAPE:  41.239924255279156

MAE:  0.22494533078932058
RMSE:  0.2524043245804403
R2:  -1.436730473078613
MAPE:  132.9085017188303
Training set size:  3145
5810
16C 1

MAE:  0.039281813309022154
RMSE:  0.04866894366196939
R2:  0.17367240787024

MAE:  0.19786269718334937
RMSE:  0.2368139752615291
R2:  -0.8391770549465625
MAPE:  inf
Training set size:  2368
9033
66X 2

MAE:  0.08131380088947215
RMSE:  0.10180326582676857
R2:  0.2984896798311799
MAPE:  24.09920605798625

MAE:  0.1685472184062022
RMSE:  0.1901722771108214
R2:  -1.4479641725363739
MAPE:  56.95880219354247
Training set size:  20054
8770
66X 1

MAE:  0.16466526094414105
RMSE:  0.19173319221452217
R2:  0.023357245409601934
MAPE:  63.48475302949781

MAE:  0.16458502186059282
RMSE:  0.18857162245086243
R2:  0.05530024674141942
MAPE:  77.04122947517459
Training set size:  14652
9159
142 1

MAE:  0.042970784154935805
RMSE:  0.05623324740769332
R2:  0.9614493750263636
MAPE:  60.7712813560581

MAE:  0.0559692218265186
RMSE:  0.06562272701153336
R2:  0.9475006843238138
MAPE:  98.68813594234379
Training set size:  21608
8486
142 2

MAE:  0.0490172283000332
RMSE:  0.06097112793976518
R2:  0.9598921681533733
MAPE:  76.2134543633049

MAE:  0.061860827666345194
RMSE:  0.07330250

Training set size:  1147
4529
33D 1

MAE:  0.15013497742515647
RMSE:  0.20906045390829536
R2:  0.030342624905623117
MAPE:  115.80972266840186

MAE:  0.35985965888135435
RMSE:  0.38891084222109984
R2:  -2.355634327779454
MAPE:  343.98896896084017
Training set size:  1517
3333
40E 1

MAE:  0.10381357346307928
RMSE:  0.152092786731271
R2:  0.1195558859526018
MAPE:  inf

MAE:  0.35854073532815256
RMSE:  0.37669998731227206
R2:  -4.401019818518207
MAPE:  inf
Training set size:  5365
3828
40E 2

MAE:  0.08935315572582433
RMSE:  0.13758235438722788
R2:  0.17910101252791322
MAPE:  45.828465040759944

MAE:  0.19915131337114883
RMSE:  0.2117796512135595
R2:  -0.9450586589492456
MAPE:  141.21499013120024
Training set size:  6364
6950
33E 1

MAE:  0.2428808449910366
RMSE:  0.24519459396555937
R2:  0.02859333217462745
MAPE:  42.120338384160796

MAE:  0.2219452271880526
RMSE:  0.2652518112428894
R2:  -0.13683128098280428
MAPE:  50.14684934114106
Training set size:  185
7659
16D 1

MAE:  0.1392688067

In [88]:
models_SVR_noDFs = list()
for model in models_SVR:
    models_SVR_noDFs += [{key:model[key] for key in model}]

In [89]:
for model in models_SVR_noDFs:
    model['columns'] = model['X_train'].columns
    model.pop('X_train')
    model.pop('X_test')
    model.pop('y_train')
    model.pop('y_test')
    model.pop('timetabled_values_train')
    model.pop('timetabled_values_test')

In [90]:
models_SVR_noDFs

[{'route': '66',
  'direction': 1,
  'model': SVR(C=1.0, cache_size=200, coef0=0.0, degree=3, epsilon=0.1, gamma='scale',
      kernel='rbf', max_iter=-1, shrinking=True, tol=0.001, verbose=False),
  'max_trip': 9416,
  'min_trip': 1799,
  'max_feels_like': 24.77,
  'min_feels_like': -13.61,
  'columns': Index(['PLANNEDTIME_DEP_COS', 'PLANNEDTIME_DEP_SIN', 'feels_like', 'month',
         'MONTH_1', 'MONTH_2', 'MONTH_3', 'MONTH_4', 'MONTH_5', 'MONTH_6',
         'MONTH_7', 'MONTH_8', 'MONTH_9', 'MONTH_10', 'MONTH_11', 'MONTH_12',
         'WEEKDAY_0', 'WEEKDAY_1', 'WEEKDAY_2', 'WEEKDAY_3', 'WEEKDAY_4',
         'WEEKDAY_5', 'WEEKDAY_6', 'WEEKEND_False', 'WEEKEND_True',
         'RUSH_HOUR_False', 'RUSH_HOUR_True', 'weather_main_Clear',
         'weather_main_Clouds', 'weather_main_Drizzle', 'weather_main_Fog',
         'weather_main_Haze', 'weather_main_Mist', 'weather_main_Rain',
         'weather_main_Smoke', 'weather_main_Snow', 'weather_main_Thunderstorm'],
        dtype='object')},

In [91]:
models_SVR

[{'route': '66',
  'direction': 1,
  'model': SVR(C=1.0, cache_size=200, coef0=0.0, degree=3, epsilon=0.1, gamma='scale',
      kernel='rbf', max_iter=-1, shrinking=True, tol=0.001, verbose=False),
  'X_train':       PLANNEDTIME_DEP_COS  PLANNEDTIME_DEP_SIN  feels_like  month  MONTH_1  \
  0               -0.537300             0.843391    0.235018      3        0   
  1                0.831470            -0.555570    0.690464      5        0   
  2               -0.980785             0.195090    0.309536     12        0   
  3               -0.173648             0.984808    0.280875      3        0   
  4               -0.751840             0.659346    0.699062      8        0   
  ...                   ...                  ...         ...    ...      ...   
  7386            -0.043619             0.999048    0.383273      4        0   
  7387            -0.422618             0.906308    0.558885      9        0   
  7388            -0.751840             0.659346    0.322043      1    

In [92]:
mname = 'models_SVR/models.pkl'
#pickle.dump(models_SVR_noDFs,open(mname,'wb'))

In [93]:
time1 = time.time()

models_LR = pool_process(mult_funcs.gen_LR_mult,dfs2_list,4)

print()
print("Seconds taken: ", time.time()-time1)

No. Inputs: 252, pool_size: 4

Seconds taken:  7.602994441986084


In [94]:
multiMetrics_mult(models_LR,'train',printall=True) 

9416
66 1

MAE:  0.04957204396019675
RMSE:  0.06615900552280575
R2:  0.5839294463846643
MAPE:  inf

MAE:  0.09621324988139365
RMSE:  0.1111208205104459
R2:  -0.17376166927810766
MAPE:  inf
Training set size:  273467
8648
66 2

MAE:  0.05216590208868783
RMSE:  0.06958207822539446
R2:  0.5024427720531356
MAPE:  inf

MAE:  0.055533650261463896
RMSE:  0.07137732134179457
R2:  0.4764372510323468
MAPE:  inf
Training set size:  234025
13531
77A 1

MAE:  0.03593666329865412
RMSE:  0.047700035896129596
R2:  0.5605122226093746
MAPE:  inf

MAE:  0.042301912926599586
RMSE:  0.057751767131129325
R2:  0.35577148325783114
MAPE:  inf
Training set size:  369075
14153
77A 2

MAE:  0.03846650464958272
RMSE:  0.05155626699764836
R2:  0.5235096444967705
MAPE:  inf

MAE:  0.08454523385904171
RMSE:  0.0955289176779554
R2:  -0.6359156269917845
MAPE:  inf
Training set size:  403522
13579
41 2

MAE:  0.03054375423829209
RMSE:  0.04194676535994558
R2:  0.4062072533842832
MAPE:  inf

MAE:  0.0683859779237865
RMSE

7 2

MAE:  0.06494787194263496
RMSE:  0.08588391392616507
R2:  0.609095377191146
MAPE:  13.56555030509709

MAE:  0.0644515876614345
RMSE:  0.08545739128739589
R2:  0.6129684111833512
MAPE:  13.708928509804426
Training set size:  246309
11861
7 1

MAE:  0.05770208544875125
RMSE:  0.08289562498972293
R2:  0.37460037304811455
MAPE:  inf

MAE:  0.10998678546630404
RMSE:  0.12982239516679892
R2:  -0.5338879375518375
MAPE:  inf
Training set size:  216672
9073
29A 2

MAE:  0.03307365886073209
RMSE:  0.04528763868003275
R2:  0.48952392829515756
MAPE:  inf

MAE:  0.08398113142242396
RMSE:  0.09239790649584918
R2:  -1.1249088157682312
MAPE:  inf
Training set size:  394013
6430
29A 1

MAE:  0.047727006898323286
RMSE:  0.062373854942993696
R2:  0.5147028937824305
MAPE:  inf

MAE:  0.1319946608620719
RMSE:  0.14385716220689515
R2:  -1.5814606401401878
MAPE:  inf
Training set size:  338328
7195
123 2

MAE:  0.05548801495314594
RMSE:  0.07319932407490796
R2:  0.42244172033996086
MAPE:  inf

MAE:  0.0

RMSE:  0.08457587640435049
R2:  0.3929709073286525
MAPE:  18.425735445418965

MAE:  0.10353103822450951
RMSE:  0.11940659607206644
R2:  -0.2099658925694512
MAPE:  33.64143104889478
Training set size:  438302
9224
25B 2

MAE:  0.05187763068328952
RMSE:  0.07015997517018961
R2:  0.4908208297701797
MAPE:  inf

MAE:  0.12696989458867813
RMSE:  0.13931033287504482
R2:  -1.007513320189147
MAPE:  inf
Training set size:  285492
7589
25B 1

MAE:  0.040453781528782436
RMSE:  0.05453347950137823
R2:  0.5720410683069574
MAPE:  inf

MAE:  0.045741490399024635
RMSE:  0.061150814881196724
R2:  0.4618787097697147
MAPE:  inf
Training set size:  323898
11321
27A 1

MAE:  0.018584576590778622
RMSE:  0.027921362344450903
R2:  0.5340108990086214
MAPE:  inf

MAE:  0.07121868283323192
RMSE:  0.07563179592226374
R2:  -2.41909663846938
MAPE:  inf
Training set size:  244755
4854
27A 2

MAE:  0.0565258968671557
RMSE:  0.07700471529801586
R2:  0.412494383498514
MAPE:  inf

MAE:  0.12664161017490252
RMSE:  0.14088

42 2

MAE:  0.04253875059270239
RMSE:  0.05841079852555886
R2:  0.43676106073868226
MAPE:  22.35488992166087

MAE:  0.10815317022527611
RMSE:  0.11753963239089321
R2:  -1.280736123622995
MAPE:  66.76416684202898
Training set size:  309024
5144
104 1

MAE:  0.0662853032745312
RMSE:  0.09093213315038016
R2:  0.33004350514663494
MAPE:  inf

MAE:  0.1126215360591937
RMSE:  0.12730171753139424
R2:  -0.31304729566106904
MAPE:  inf
Training set size:  77922
5286
104 2

MAE:  0.07651861622104286
RMSE:  0.1064491689618398
R2:  0.24493093504765018
MAPE:  inf

MAE:  0.15734857158575702
RMSE:  0.17213299419764852
R2:  -0.9743783200150733
MAPE:  inf
Training set size:  98050
9768
63 2

MAE:  0.03238161487165214
RMSE:  0.04509813616389898
R2:  0.3708877843322278
MAPE:  inf

MAE:  0.035319443490260005
RMSE:  0.050810467205106034
R2:  0.20142206259230921
MAPE:  inf
Training set size:  181707
7828
63 1

MAE:  0.04851840459387806
RMSE:  0.06350777384344732
R2:  0.4189867463562702
MAPE:  18.6256842777414

79 1

MAE:  0.029755278958454066
RMSE:  0.04534473175251302
R2:  0.4147405578773392
MAPE:  11.144118334816646

MAE:  0.032661908544723284
RMSE:  0.049858003009039115
R2:  0.2924379788889365
MAPE:  11.379989655125678
Training set size:  287823
6589
45A 1

MAE:  0.050720346870406365
RMSE:  0.06656869143868382
R2:  0.6003254439385843
MAPE:  10.805921526735048

MAE:  0.052527243928154936
RMSE:  0.06933015553325345
R2:  0.5664783307259009
MAPE:  11.349785819040454
Training set size:  192881
6952
45A 2

MAE:  0.06896088204429297
RMSE:  0.09249235511115939
R2:  0.5294250321822578
MAPE:  inf

MAE:  0.1280156684766695
RMSE:  0.1473937660256601
R2:  -0.19502055782548489
MAPE:  inf
Training set size:  193954
12644
1 1

MAE:  0.03355937005450386
RMSE:  0.04407104613747852
R2:  0.49844032227526147
MAPE:  inf

MAE:  0.03340868707367012
RMSE:  0.04084954489867853
R2:  0.5690862619381953
MAPE:  inf
Training set size:  418692
23458
1 2

MAE:  0.019134395573587176
RMSE:  0.025033494873460703
R2:  0.4933

238 2

MAE:  0.03897693340751015
RMSE:  0.05521267373936861
R2:  0.33563124284481327
MAPE:  inf

MAE:  0.0476484252171279
RMSE:  0.06664125708683977
R2:  0.032127824719740294
MAPE:  inf
Training set size:  100233
7846
220 1

MAE:  0.08066115921945083
RMSE:  0.10325344299030174
R2:  0.4418907121011817
MAPE:  inf

MAE:  0.21372540275280583
RMSE:  0.23436921929421217
R2:  -1.8754863637638213
MAPE:  inf
Training set size:  51948
10881
220 2

MAE:  0.04316414027383827
RMSE:  0.06640585204187872
R2:  0.3275209853139177
MAPE:  inf

MAE:  0.12194951212671105
RMSE:  0.13725080915290266
R2:  -1.8727369235117362
MAPE:  inf
Training set size:  57239
5880
33A 2

MAE:  0.08130712216170378
RMSE:  0.1069521508195259
R2:  0.7031412206239018
MAPE:  inf

MAE:  0.14027368756962577
RMSE:  0.1621148335917368
R2:  0.31794976695523103
MAPE:  inf
Training set size:  45473
5266
33A 1

MAE:  0.05860908890942674
RMSE:  0.08274901479562592
R2:  0.3195372562751462
MAPE:  inf

MAE:  0.12262248112596492
RMSE:  0.1442

R2:  0.2541818413156549
MAPE:  inf
Training set size:  34447
3075
236 1

MAE:  0.083730602448864
RMSE:  0.11554945337125583
R2:  0.47142858794163367
MAPE:  31.61729222743524

MAE:  0.18942860596331135
RMSE:  0.23207140263402748
R2:  -1.1321174967920427
MAPE:  91.27710236912029
Training set size:  16021
4426
236 2

MAE:  0.07108822118703578
RMSE:  0.10615598617855435
R2:  0.33263306271291104
MAPE:  inf

MAE:  0.18669954461657456
RMSE:  0.21268664004477505
R2:  -1.6788977006826182
MAPE:  inf
Training set size:  11951
6408
39X 2

MAE:  0.06889814320370641
RMSE:  0.0908563124389728
R2:  0.5643193130714987
MAPE:  inf

MAE:  0.20224571783526432
RMSE:  0.22526270043953056
R2:  -1.678160919989896
MAPE:  inf
Training set size:  22866
9681
39X 1

MAE:  0.057863668361966714
RMSE:  0.08428167708232619
R2:  0.36291211605332785
MAPE:  inf

MAE:  0.23827949090427492
RMSE:  0.25448878072441655
R2:  -4.8085842121054405
MAPE:  inf
Training set size:  12950
5056
114 1

MAE:  0.05785046582017656
RMSE:  0.

R2:  -4.004706497802663
MAPE:  105.3182309107126
Training set size:  18981
6312
15D 2

MAE:  0.11628371654636602
RMSE:  0.15211900664513803
R2:  0.44141812990797047
MAPE:  inf

MAE:  0.20716716533977317
RMSE:  0.2552137322263254
R2:  -0.5722729817937102
MAPE:  inf
Training set size:  4144
5747
15D 1

MAE:  0.08173610690856602
RMSE:  0.10802214554151239
R2:  0.5810237501856619
MAPE:  30.1200155410248

MAE:  0.22772276491511836
RMSE:  0.25936236162567905
R2:  -1.4153368711953709
MAPE:  111.13819893683568
Training set size:  9916
6865
25X 2

MAE:  0.08889855695799823
RMSE:  0.12069652980624197
R2:  0.46485216498907855
MAPE:  inf

MAE:  0.3118321539768928
RMSE:  0.3359586605658884
R2:  -3.1462538480253786
MAPE:  inf
Training set size:  5032
8082
25X 1

MAE:  0.06950149022105186
RMSE:  0.08932729270485834
R2:  0.4330303607499014
MAPE:  inf

MAE:  0.2479681598684547
RMSE:  0.26950675270847196
R2:  -4.1609632002496415
MAPE:  inf
Training set size:  9916
4080
68A 2

MAE:  0.10085176598157874
R

In [95]:
multiMetrics_mult(models_LR,'test',printall=True) 

9416
66 1

MAE:  0.05154522298572826
RMSE:  0.0683084984581209
R2:  0.5671530248798021
MAPE:  16.354201400379324

MAE:  0.09790810558239944
RMSE:  0.11274856703018793
R2:  -0.1792529491095709
MAPE:  35.73951947314073
Training set size:  117216
8648
66 2

MAE:  0.05163229876525752
RMSE:  0.06915734813201167
R2:  0.48189406594967743
MAPE:  13.608554748221918

MAE:  0.05435277724987438
RMSE:  0.06919509929100827
R2:  0.48132827103653375
MAPE:  14.874871736128693
Training set size:  100344
13531
77A 1

MAE:  0.0358516227176162
RMSE:  0.04667094502586304
R2:  0.5797734117721568
MAPE:  10.688655436692587

MAE:  0.04264095477755587
RMSE:  0.0578567514712681
R2:  0.3541994238185312
MAPE:  11.866261310805818
Training set size:  158175
14153
77A 2

MAE:  0.03794677313317968
RMSE:  0.05027069850985061
R2:  0.5368976083774303
MAPE:  18.925541810647864

MAE:  0.08446545961709591
RMSE:  0.09519766455602581
R2:  -0.6607328359148186
MAPE:  47.232160962931424
Training set size:  172938
13579
41 2

MAE:

11861
7 1

MAE:  0.056030471108990225
RMSE:  0.08049141135682604
R2:  0.3889969505919818
MAPE:  29.569588610578755

MAE:  0.1082873585349119
RMSE:  0.12781856768980662
R2:  -0.5407500340420346
MAPE:  65.39381596419287
Training set size:  92870
9073
29A 2

MAE:  0.03303776573957265
RMSE:  0.044310706600216715
R2:  0.4973558277593626
MAPE:  20.498834301022733

MAE:  0.08330409007283344
RMSE:  0.09124635993407382
R2:  -1.1314463080201564
MAPE:  60.44923506991518
Training set size:  168868
6430
29A 1

MAE:  0.04850988565958735
RMSE:  0.06384289227317634
R2:  0.4997216375886303
MAPE:  25.294939077202155

MAE:  0.1304047204284108
RMSE:  0.14285971872717623
R2:  -1.5049911378984593
MAPE:  77.15559189233325
Training set size:  145040
7195
123 2

MAE:  0.05602689859300149
RMSE:  0.07339201771507811
R2:  0.4326044896147697
MAPE:  16.963407180984934

MAE:  0.05456426031484031
RMSE:  0.06997645866505511
R2:  0.48418714650247074
MAPE:  13.329177538861439
Training set size:  238798
8675
123 1

MAE: 

145 2

MAE:  0.03714192871345439
RMSE:  0.04940980629746557
R2:  0.4231364885633897
MAPE:  12.878042342036006

MAE:  0.044369045453038325
RMSE:  0.053357712982486635
R2:  0.32726940432998275
MAPE:  13.04471242399641
Training set size:  296814
12770
145 1

MAE:  0.0405587340197445
RMSE:  0.058433230210928847
R2:  0.3413445453274926
MAPE:  12.803731290820918

MAE:  0.03588802969078285
RMSE:  0.0479653414609787
R2:  0.5561935762994307
MAPE:  9.628240849422651
Training set size:  307544
9314
39A 2

MAE:  0.0628435455366658
RMSE:  0.08201266907949643
R2:  0.4880474168058353
MAPE:  26.772229100526452

MAE:  0.08010626843896407
RMSE:  0.09571421096207544
R2:  0.3026983490371383
MAPE:  31.026728446281332
Training set size:  272542
10935
39A 1

MAE:  0.04962694274553746
RMSE:  0.06627575990686471
R2:  0.5496547396793728
MAPE:  17.525296934164448

MAE:  0.04956727701335702
RMSE:  0.06491269127337561
R2:  0.567988413196192
MAPE:  12.349433491939491
Training set size:  237207
9600
15B 2

MAE:  0.0

68 1

MAE:  0.048708681379926504
RMSE:  0.06831133741699547
R2:  0.46228132569263236
MAPE:  14.629023209786515

MAE:  0.05905741266476095
RMSE:  0.07391402865843812
R2:  0.3704600562118253
MAPE:  19.438454707712232
Training set size:  58497
7625
68 2

MAE:  0.0809796884431176
RMSE:  0.10338719200645238
R2:  0.5637200163355995
MAPE:  31.449076327414637

MAE:  0.07644659738408287
RMSE:  0.09627655983551246
R2:  0.6216681227649365
MAPE:  33.66647179757323
Training set size:  53983
9548
66A 2

MAE:  0.04931652639699102
RMSE:  0.07092646615657403
R2:  0.2875649297040239
MAPE:  34.00831106379415

MAE:  0.11992656184514888
RMSE:  0.13201388181750368
R2:  -1.4681289648027263
MAPE:  99.17659496454382
Training set size:  43364
16871
66A 1

MAE:  0.023191726173379026
RMSE:  0.031017805961947253
R2:  0.4645422221996198
MAPE:  24.893840312754666

MAE:  0.07039535806428322
RMSE:  0.07575957375120657
R2:  -2.1943178376356993
MAPE:  87.13708261538332
Training set size:  52947
10955
76 1

MAE:  0.03612

MAPE:  32.17146728028038
Training set size:  171828
8546
59 1

MAE:  0.014246557966100276
RMSE:  0.01889290304289825
R2:  0.43639389039234067
MAPE:  inf

MAE:  0.04719522706174104
RMSE:  0.05075269127618671
R2:  -3.0672086636725373
MAPE:  inf
Training set size:  46879
3517
59 2

MAE:  0.047352686889088155
RMSE:  0.0672563814527736
R2:  0.37120213366926325
MAPE:  inf

MAE:  0.1151464866607869
RMSE:  0.1250139354608771
R2:  -1.1725056687953548
MAPE:  inf
Training set size:  47101
9862
70 2

MAE:  0.06325105749089932
RMSE:  0.08245767230095115
R2:  0.41462455198148496
MAPE:  32.51267436484036

MAE:  0.09777427385807393
RMSE:  0.11305266414450979
R2:  -0.10035789457602817
MAPE:  52.29742315556245
Training set size:  59940
9864
70 1

MAE:  0.06683926157684343
RMSE:  0.08272140398876941
R2:  0.49506889896368544
MAPE:  30.25873438491083

MAE:  0.13179533689001444
RMSE:  0.15230245621705563
R2:  -0.7116309965997307
MAPE:  73.2642888581931
Training set size:  70448
10278
184 1

MAE:  0.02115741

RMSE:  0.10654066993982338
R2:  0.37171278025788057
MAPE:  31.365547380608668

MAE:  0.21940464083454833
RMSE:  0.24046288725710813
R2:  -2.200541727626873
MAPE:  91.86712247847714
Training set size:  22311
10881
220 2

MAE:  0.04246389947327534
RMSE:  0.05471298589616517
R2:  0.3594329600085261
MAPE:  18.29718140463177

MAE:  0.11690217195952006
RMSE:  0.13052773312940585
R2:  -2.645770671099135
MAPE:  53.26988861153572
Training set size:  24568
5880
33A 2

MAE:  0.08715965066664919
RMSE:  0.1180490657571365
R2:  0.649908152161331
MAPE:  211.98993166741883

MAE:  0.13883281924270408
RMSE:  0.16307610789858956
R2:  0.33190601063277947
MAPE:  96.8258579415945
Training set size:  19499
5266
33A 1

MAE:  0.06079156570074445
RMSE:  0.08511293233539063
R2:  0.2836999792866004
MAPE:  10.026704304961923

MAE:  0.1238639136765482
RMSE:  0.14744670012882918
R2:  -1.1496807734376864
MAPE:  18.603439828859003
Training set size:  12950
6825
41B 1

MAE:  0.06272320078777341
RMSE:  0.081196324510271

R2:  0.22640206002415408
MAPE:  36.08840026583282

MAE:  0.1729718544075378
RMSE:  0.19324771536769833
R2:  -2.3313118360287834
MAPE:  124.05277985717453
Training set size:  5143
6408
39X 2

MAE:  0.07857835257003165
RMSE:  0.10878793987043403
R2:  0.47392374092814826
MAPE:  21.954871333812147

MAE:  0.21063949653407266
RMSE:  0.23210337791951624
R2:  -1.3946945190536404
MAPE:  68.58599198828857
Training set size:  9842
9681
39X 1

MAE:  0.05849065779667962
RMSE:  0.08062601326943328
R2:  0.3254918667219452
MAPE:  26.55926460826774

MAE:  0.23639784171692985
RMSE:  0.24960900837323138
R2:  -5.464833278385935
MAPE:  126.00451956753453
Training set size:  5550
5056
114 1

MAE:  0.054951373113443544
RMSE:  0.07379553281179525
R2:  0.44072609831460785
MAPE:  37.802914630187104

MAE:  0.1325520293442696
RMSE:  0.1449905705531881
R2:  -1.1589566682288224
MAPE:  105.55461755454844
Training set size:  46028
8273
114 2

MAE:  0.03636594123135271
RMSE:  0.05069753634178812
R2:  0.405400528267765

41X 2

MAE:  0.08896962030013879
RMSE:  0.11162372119289349
R2:  0.133612586329665
MAPE:  25.845568689885862

MAE:  0.13111046039167978
RMSE:  0.14679769058150977
R2:  -0.4984338945432396
MAPE:  41.65827019129381
Training set size:  13875
8521
41X 1

MAE:  0.0758193605371933
RMSE:  0.10083842698462216
R2:  0.1786972243978242
MAPE:  inf

MAE:  0.09409215885068277
RMSE:  0.11844656745321326
R2:  -0.1331727568273704
MAPE:  inf
Training set size:  9731
5444
44B 1

MAE:  0.037003427402535025
RMSE:  0.04940749851046125
R2:  0.3946062976799929
MAPE:  11.979742944086908

MAE:  0.04919984484816295
RMSE:  0.06703140723792222
R2:  -0.11431721584662502
MAPE:  15.107907723747354
Training set size:  12358
3686
44B 2

MAE:  0.07340615474159662
RMSE:  0.09905809512558747
R2:  0.12279110074770783
MAPE:  inf

MAE:  0.19689921991795736
RMSE:  0.21486482577633217
R2:  -3.1271830902610027
MAPE:  inf
Training set size:  11840
4099
31D 2

MAE:  417096775.49108326
RMSE:  2147137066.0171037
R2:  -1.17444036285

In [96]:
time1 = time.time()

models_KNR = pool_process(mult_funcs.gen_KNR_mult,dfs2_list,4)

print()
print("Seconds taken: ", time.time()-time1)

No. Inputs: 252, pool_size: 4

Seconds taken:  15.535996198654175


In [97]:
multiMetrics_mult(models_KNR,'train') 

9416
8648
13531
14153
13579
9445
11430
8640
11027
6252
10181
14277
10201
8344
10188
13978
12552
12222
10323
10792
9422
10415
10804
11737
8858
10319
9224
10271
8395
12507
7620
11861
9073
6430
7195
8675
11668
13502
12888
9779
8660
7728
9270
10253
12335
12957
17375
10031
12815
11879
12138
14325
7332
12041
9912
16262
13215
9855
9224
7589
11321
4854
16040
12770
9314
10935
9600
8681
6160
6253
6356
6379
6540
6543
10651
10236
9189
8450
7647
7392
16011
8616
10385
9652
9464
8442
16083
9400
6873
6871
9112
9326
5144
5286
9768
7828
10100
7625
9548
16871
10955
7503
8865
8613
13861
13655
9911
10014
4817
5815
10267
10002
4145
9748
6204
6239
7341
8493
9444
7604
9662
9083
9752
11463
7071
7557
6589
6952
12644
23458
5444
6689
8546
3517
9862
9864
10278
6612
9995
10226
12122
9885
7596
7970
11008
8867
4787
7051
8947
5755
7007
8411
4552
9007
7893
6457
7816
4398
7846
10881
5880
5266
6825
5296
5550
6068
6216
5647
3726
5810
5916
5158
9814
7397
7379
7128
8830
7979
6499
6659
10569
7786
5691
10783
8848
10488
7237
7

In [98]:
multiMetrics_mult(models_KNR,'test') 

9416
8648
13531
14153
13579
9445
11430
8640
11027
6252
10181
14277
10201
8344
10188
13978
12552
12222
10323
10792
9422
10415
10804
11737
8858
10319
9224
10271
8395
12507
7620
11861
9073
6430
7195
8675
11668
13502
12888
9779
8660
7728
9270
10253
12335
12957
17375
10031
12815
11879
12138
14325
7332
12041
9912
16262
13215
9855
9224
7589
11321
4854
16040
12770
9314
10935
9600
8681
6160
6253
6356
6379
6540
6543
10651
10236
9189
8450
7647
7392
16011
8616
10385
9652
9464
8442
16083
9400
6873
6871
9112
9326
5144
5286
9768
7828
10100
7625
9548
16871
10955
7503
8865
8613
13861
13655
9911
10014
4817
5815
10267
10002
4145
9748
6204
6239
7341
8493
9444
7604
9662
9083
9752
11463
7071
7557
6589
6952
12644
23458
5444
6689
8546
3517
9862
9864
10278
6612
9995
10226
12122
9885
7596
7970
11008
8867
4787
7051
8947
5755
7007
8411
4552
9007
7893
6457
7816
4398
7846
10881
5880
5266
6825
5296
5550
6068
6216
5647
3726
5810
5916
5158
9814
7397
7379
7128
8830
7979
6499
6659
10569
7786
5691
10783
8848
10488
7237
7

### Improvements with KNN models?

In [99]:
def gen_KNR(df,n_neighbors=5,verbose=False):
    import pandas as pd
    from sklearn.model_selection import train_test_split
    from sklearn.neural_network import MLPRegressor
    from sklearn.svm import SVR
    from sklearn.linear_model import LinearRegression
    from sklearn.neighbors import KNeighborsRegressor

    route = df['LINEID'].unique()[0]
    direction = df['DIRECTION'].unique()[0]
    max_trip = df['TRIPLENGTH'].max()
    
    print(df['TRIPLENGTH'].min(),df['TRIPLENGTH'].max())
    
#     df['TRIPLENGTH'] = (df['TRIPLENGTH'] - df['TRIPLENGTH'].min())/(df['TRIPLENGTH'].max() - df['TRIPLENGTH'].min())
#     df['feels_like'] = (df['feels_like'] - df['feels_like'].min())/(df['feels_like'].max() - df['feels_like'].min())
    
    df_rev1 = pd.get_dummies(df.drop(['LINEID','DIRECTION'],axis=1))
        
#   print(route, direction)
    # y is the target
    y = (df_rev1['TRIPLENGTH'] - df_rev1['TRIPLENGTH'].min())/(df_rev1['TRIPLENGTH'].max() - df_rev1['TRIPLENGTH'].min())
    # X is everything else
    X = df_rev1.drop(["TRIPLENGTH"],1)
    X['feels_like'] = (X['feels_like'] - X['feels_like'].min())/(X['feels_like'].max() - X['feels_like'].min())
    # Split the dataset into two datasets: 70% training and 30% test
    X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1,  test_size=0.3)

#   timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
#   timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
            
#   X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
#   X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
#   X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
#   X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
            
#   print("original range is: ",df_rev1.shape[0])
#   print("training range (70%):\t rows 0 to", round(X_train.shape[0]))
#   print("test range (30%): \t rows", round(X_train.shape[0]), "to", round(X_train.shape[0]) + X_test.shape[0])
            
# need to reset the index to allow contatenation with predicted values otherwise not joining on same index...
    X_train.reset_index(drop=True, inplace=True)
    y_train.reset_index(drop=True, inplace=True)
    X_test.reset_index(drop=True, inplace=True)
    y_test.reset_index(drop=True, inplace=True)
    X_train.head(5)
        
    timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
    timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
    X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    
    output_model = KNeighborsRegressor(n_neighbors=n_neighbors).fit(X_train,y_train)
    
#     test_train_dict[key] = {
#                 'X_train':X_train,
#                 'X_test':X_test,
#                 'y_train':y_train,
#                 'y_test':y_test,
#                 'timetabled_values_train':timetabled_values_train,
#                 'timetabled_values_test':timetabled_values_test
#             }
    
    
    output = {
        'route':route,
        'direction':direction,
        'model':output_model,
        'X_train':X_train,
        'X_test':X_test,
        'y_train':y_train,
        'y_test':y_test,
        'timetabled_values_train':timetabled_values_train/max_trip,
        'timetabled_values_test':timetabled_values_test/max_trip,
        'max_trip':max_trip
    }
    if verbose == True:
        print('Done: \t%s\t%s'%(route,direction))
    return output

In [100]:
warnings.filterwarnings('ignore')

time1 = time.time()

models_KNR = []
for df in dfs2_list:
    models_KNR += [gen_KNR(df,n_neighbors=8,verbose=True)]

print()
print("Seconds taken: ", time.time()-time1)

1799 9416
Done: 	66	1
1001 8648
Done: 	66	2
118 13531
Done: 	77A	1
1877 14153
Done: 	77A	2
1377 13579
Done: 	41	2
544 9445
Done: 	41	1
1078 11430
Done: 	83	1
880 8640
Done: 	83	2
371 11027
Done: 	130	2
579 6252
Done: 	130	1
804 10181
Done: 	40	1
741 14277
Done: 	40	2
371 10201
Done: 	151	2
518 8344
Done: 	151	1
945 10188
Done: 	13	1
431 13978
Done: 	13	2
20 12552
Done: 	75	1
1762 12222
Done: 	75	2
1251 10323
Done: 	65	1
2435 10792
Done: 	65	2
914 9422
Done: 	122	2
596 10415
Done: 	122	1
971 10804
Done: 	33	2
2618 11737
Done: 	33	1
51 8858
Done: 	41C	1
447 10319
Done: 	41C	2
897 9224
Done: 	7A	1
1846 10271
Done: 	7A	2
68 8395
Done: 	67	2
2450 12507
Done: 	67	1
585 7620
Done: 	7	2
2301 11861
Done: 	7	1
1101 9073
Done: 	29A	2
1277 6430
Done: 	29A	1
518 7195
Done: 	123	2
1007 8675
Done: 	123	1
1268 11668
Done: 	27	2
1116 13502
Done: 	27	1
805 12888
Done: 	16	1
2599 9779
Done: 	16	2
126 8660
Done: 	150	1
1226 7728
Done: 	150	2
40 9270
Done: 	4	1
303 10253
Done: 	4	2
1017 12335
Done: 	15	1
1

In [101]:
models_KNR[0]

{'route': '66',
 'direction': 1,
 'model': KNeighborsRegressor(algorithm='auto', leaf_size=30, metric='minkowski',
                     metric_params=None, n_jobs=None, n_neighbors=8, p=2,
                     weights='uniform'),
 'X_train':       PLANNEDTIME_DEP_COS  PLANNEDTIME_DEP_SIN  feels_like  month  MONTH_1  \
 0               -0.537300             0.843391    0.235018      3        0   
 1                0.831470            -0.555570    0.690464      5        0   
 2               -0.980785             0.195090    0.309536     12        0   
 3               -0.173648             0.984808    0.280875      3        0   
 4               -0.751840             0.659346    0.699062      8        0   
 ...                   ...                  ...         ...    ...      ...   
 7386            -0.043619             0.999048    0.383273      4        0   
 7387            -0.422618             0.906308    0.558885      9        0   
 7388            -0.751840             0.659346 

In [102]:
multiMetrics_mult(models_KNR,'train') 

KeyError: 'min_trip'

In [ ]:
warnings.filterwarnings('ignore')

time1 = time.time()

models_KNR = []
for df in dfs2_list:
    models_KNR += [gen_KNR(df,n_neighbors=20,verbose=True)]

print()
print("Seconds taken: ", time.time()-time1)

In [ ]:
multiMetrics_mult(models_KNR,'test') 

In [ ]:
warnings.filterwarnings('ignore')

time1 = time.time()

models_KNR = []
for df in dfs2_list:
    models_KNR += [gen_KNR(df,n_neighbors=30,verbose=True)]

print()
print("Seconds taken: ", time.time()-time1)

In [ ]:
multiMetrics_mult(models_KNR,'test') 

In [ ]:
warnings.filterwarnings('ignore')

time1 = time.time()

models_KNR = []
for df in dfs2_list:
    models_KNR += [gen_KNR(df,n_neighbors=50,verbose=True)]

print()
print("Seconds taken: ", time.time()-time1)

In [ ]:
multiMetrics_mult(models_KNR,'test') 

### KNN with large number of neighbours is waaaaaay too slow

In [103]:
import xgboost as xgb

In [104]:
def gen_xgb(df,verbose=False):
    import pandas as pd
    from sklearn.model_selection import train_test_split
    from sklearn.neural_network import MLPRegressor
    from sklearn.svm import SVR
    from sklearn.linear_model import LinearRegression
    from sklearn.neighbors import KNeighborsRegressor

    route = df['LINEID'].unique()[0]
    direction = df['DIRECTION'].unique()[0]
    max_trip = df['TRIPLENGTH'].max()
    
    print(df['TRIPLENGTH'].min(),df['TRIPLENGTH'].max())
    
#     df['TRIPLENGTH'] = (df['TRIPLENGTH'] - df['TRIPLENGTH'].min())/(df['TRIPLENGTH'].max() - df['TRIPLENGTH'].min())
#     df['feels_like'] = (df['feels_like'] - df['feels_like'].min())/(df['feels_like'].max() - df['feels_like'].min())
    
    df_rev1 = pd.get_dummies(df.drop(['LINEID','DIRECTION'],axis=1))
        
#   print(route, direction)
    # y is the target
    y = (df_rev1['TRIPLENGTH'] - df_rev1['TRIPLENGTH'].min())/(df_rev1['TRIPLENGTH'].max() - df_rev1['TRIPLENGTH'].min())
    # X is everything else
    X = df_rev1.drop(["TRIPLENGTH"],1)
    X['feels_like'] = (X['feels_like'] - X['feels_like'].min())/(X['feels_like'].max() - X['feels_like'].min())
    # Split the dataset into two datasets: 70% training and 30% test
    X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=1,  test_size=0.3)

#   timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
#   timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
            
#   X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
#   X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
#   X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
#   X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
            
#   print("original range is: ",df_rev1.shape[0])
#   print("training range (70%):\t rows 0 to", round(X_train.shape[0]))
#   print("test range (30%): \t rows", round(X_train.shape[0]), "to", round(X_train.shape[0]) + X_test.shape[0])
            
# need to reset the index to allow contatenation with predicted values otherwise not joining on same index...
    X_train.reset_index(drop=True, inplace=True)
    y_train.reset_index(drop=True, inplace=True)
    X_test.reset_index(drop=True, inplace=True)
    y_test.reset_index(drop=True, inplace=True)
    X_train.head(5)
        
    timetabled_values_train = X_train['PLANNEDTIME_ARR'] - X_train['PLANNEDTIME_DEP']
    timetabled_values_test = X_test['PLANNEDTIME_ARR'] - X_test['PLANNEDTIME_DEP']
    X_train.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    X_test.drop('PLANNEDTIME_ARR',axis=1,inplace=True)
    X_train.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    X_test.drop('PLANNEDTIME_DEP',axis=1,inplace=True)
    
    D_train = xgb.DMatrix(X_train, label=y_train)
    D_test = xgb.DMatrix(X_test, label=y_test)
    
    param = {
    'eta': 0.3, 
    'objective': 'reg:squaredlogerror',
    'max_depth':20
    } 

    steps = 20  # The number of training iterations

    
    output_model = xgb.train(param, D_train, steps)

    
#     test_train_dict[key] = {
#                 'X_train':X_train,
#                 'X_test':X_test,
#                 'y_train':y_train,
#                 'y_test':y_test,
#                 'timetabled_values_train':timetabled_values_train,
#                 'timetabled_values_test':timetabled_values_test
#             }
    
    
    output = {
        'route':route,
        'direction':direction,
        'model':output_model,
        'D_test':D_test,
        'D_train':D_train,
        'X_train':X_train,
        'X_test':X_test,
        'y_train':y_train,
        'y_test':y_test,
        'timetabled_values_train':timetabled_values_train/max_trip,
        'timetabled_values_test':timetabled_values_test/max_trip,
        'max_trip':max_trip
    }
    if verbose == True:
        print('Done: \t%s\t%s'%(route,direction))
    return output

In [105]:
warnings.filterwarnings('ignore')

time1 = time.time()

models_xgb = []
for df in dfs2_list:
    models_xgb += [gen_xgb(df,verbose=True)]

print()
print("Seconds taken: ", time.time()-time1)

1799 9416
Done: 	66	1
1001 8648
Done: 	66	2
118 13531
Done: 	77A	1
1877 14153
Done: 	77A	2
1377 13579
Done: 	41	2
544 9445
Done: 	41	1
1078 11430
Done: 	83	1
880 8640
Done: 	83	2
371 11027
Done: 	130	2
579 6252
Done: 	130	1
804 10181
Done: 	40	1
741 14277
Done: 	40	2
371 10201
Done: 	151	2
518 8344
Done: 	151	1
945 10188
Done: 	13	1
431 13978
Done: 	13	2
20 12552
Done: 	75	1
1762 12222
Done: 	75	2
1251 10323
Done: 	65	1
2435 10792
Done: 	65	2
914 9422
Done: 	122	2
596 10415
Done: 	122	1
971 10804
Done: 	33	2
2618 11737
Done: 	33	1
51 8858
Done: 	41C	1
447 10319
Done: 	41C	2
897 9224
Done: 	7A	1
1846 10271
Done: 	7A	2
68 8395
Done: 	67	2
2450 12507
Done: 	67	1
585 7620
Done: 	7	2
2301 11861
Done: 	7	1
1101 9073
Done: 	29A	2
1277 6430
Done: 	29A	1
518 7195
Done: 	123	2
1007 8675
Done: 	123	1
1268 11668
Done: 	27	2
1116 13502
Done: 	27	1
805 12888
Done: 	16	1
2599 9779
Done: 	16	2
126 8660
Done: 	150	1
1226 7728
Done: 	150	2
40 9270
Done: 	4	1
303 10253
Done: 	4	2
1017 12335
Done: 	15	1
1

In [106]:
models_xgb

[{'route': '66',
  'direction': 1,
  'model': <xgboost.core.Booster at 0x1d11cb382c8>,
  'D_test': <xgboost.core.DMatrix at 0x1d11cb4d108>,
  'D_train': <xgboost.core.DMatrix at 0x1d11cb4aa88>,
  'X_train':       PLANNEDTIME_DEP_COS  PLANNEDTIME_DEP_SIN  feels_like  month  MONTH_1  \
  0               -0.537300             0.843391    0.235018      3        0   
  1                0.831470            -0.555570    0.690464      5        0   
  2               -0.980785             0.195090    0.309536     12        0   
  3               -0.173648             0.984808    0.280875      3        0   
  4               -0.751840             0.659346    0.699062      8        0   
  ...                   ...                  ...         ...    ...      ...   
  7386            -0.043619             0.999048    0.383273      4        0   
  7387            -0.422618             0.906308    0.558885      9        0   
  7388            -0.751840             0.659346    0.322043      1        

In [107]:
def xgb_Metrics(models):
    import numpy as np
    from sklearn.metrics import precision_score, recall_score, accuracy_score
    for model in models:
        y_test = model['y_test']
        preds = model['model'].predict(model['D_test'])
        best_preds = np.asarray([np.argmax(line) for line in preds])
        print(model['route'] + " - " + str(model['direction']))
        print('---')
        print('RMSE = {}'.format(metrics.mean_squared_error(y_test,best_preds)))
#         print("Precision = {}".format(precision_score(y_test, best_preds, average='macro')))
#         print("Recall = {}".format(recall_score(y_test, best_preds, average='macro')))
#         print("Accuracy = {}".format(accuracy_score(y_test, best_preds)))
        print()

In [108]:
xgb_Metrics(models_xgb)

66 - 1
---
RMSE = 0.1259816182654715

66 - 2
---
RMSE = 0.1649554737292567

77A - 1
---
RMSE = 0.12632835615192517

77A - 2
---
RMSE = 0.05960453843534931

41 - 2
---
RMSE = 0.040647779099993

41 - 1
---
RMSE = 0.11353452213737057

83 - 1
---
RMSE = 0.14116201051020888

83 - 2
---
RMSE = 0.24550863744686702

130 - 2
---
RMSE = 0.021589414295275035

130 - 1
---
RMSE = 0.05230481710994693

40 - 1
---
RMSE = 0.2829243974960034

40 - 2
---
RMSE = 0.1306256189276483

151 - 2
---
RMSE = 0.11720212183198636

151 - 1
---
RMSE = 0.1932973200276538

13 - 1
---
RMSE = 0.33402258511449934

13 - 2
---
RMSE = 0.18004210222262823

75 - 1
---
RMSE = 0.14159656941924165

75 - 2
---
RMSE = 0.09646968281317009

65 - 1
---
RMSE = 0.16497731834339857

65 - 2
---
RMSE = 0.13516960289301394

122 - 2
---
RMSE = 0.13779241925885904

122 - 1
---
RMSE = 0.11214506096459617

33 - 2
---
RMSE = 0.22058396683084713

33 - 1
---
RMSE = 0.12831259963489175

41C - 1
---
RMSE = 0.18607018925603075

41C - 2
---
RMSE = 0.1

69X - 1
---
RMSE = 0.2159735647225386

27X - 2
---
RMSE = 0.2823474137339826

27X - 1
---
RMSE = 0.17545824357030176

38D - 1
---
RMSE = 0.2320611546918876

38D - 2
---
RMSE = 0.30992169428104166

46E - 2
---
RMSE = 0.1790926578249791

41X - 2
---
RMSE = 0.16080815987717523

41X - 1
---
RMSE = 0.27152148222608385

44B - 1
---
RMSE = 0.10258702598693241

44B - 2
---
RMSE = 0.07816854154404104

31D - 2
---
RMSE = 0.18366698098128492

31D - 1
---
RMSE = 0.08587418919001119

25D - 2
---
RMSE = 0.1328902856565512

25D - 1
---
RMSE = 0.07694292209085499

15D - 2
---
RMSE = 0.2680981543643744

15D - 1
---
RMSE = 0.14266315889889672

25X - 2
---
RMSE = 0.11390899515708956

25X - 1
---
RMSE = 0.1305697855442643

68A - 2
---
RMSE = 0.1912556919991412

68A - 1
---
RMSE = 0.0903829096694674

14C - 2
---
RMSE = 0.14086197487449198

14C - 1
---
RMSE = 0.09347977172543091

116 - 2
---
RMSE = 0.26573933378575454

116 - 1
---
RMSE = 0.2146374802383621

118 - 2
---
RMSE = 0.24191895330114624

161 - 2
--

In [109]:
models_xgb[0]['D_test']

In [110]:
dftrips_fresh = pd.read_csv('../../data/rt_trips_DB_2018.txt',sep=';')

dftrips_fresh.head()

DATASOURCE        DAYOFSERVICE   TRIPID LINEID  ROUTEID  DIRECTION  \
0         DB  07-FEB-18 00:00:00  6253783     68    68_80          1   
1         DB  07-FEB-18 00:00:00  6262138    25B  25B_271          2   
2         DB  07-FEB-18 00:00:00  6254942    45A   45A_70          2   
3         DB  07-FEB-18 00:00:00  6259460    25A  25A_273          1   
4         DB  07-FEB-18 00:00:00  6253175     14    14_15          1   

   PLANNEDTIME_ARR  PLANNEDTIME_DEP  ACTUALTIME_ARR  ACTUALTIME_DEP   BASIN  \
0            87245            84600         87524.0         84600.0  BasDef   
1            30517            26460         32752.0             NaN  BasDef   
2            35512            32100         36329.0         32082.0  BasDef   
3            57261            54420         58463.0         54443.0  BasDef   
4            85383            81600         84682.0         81608.0  BasDef   

   TENDERLOT  SUPPRESSED  JUSTIFICATIONID          LASTUPDATE       NOTE  
0        NaN         NaN              NaN  28-FEB-18 12:05:11  ,2967409,  
1        NaN         NaN              NaN  28-FEB-18 12:05:11  ,2580260,  
2        NaN         NaN              NaN  28-FEB-18 12:05:11  ,2448968,  
3        NaN         NaN              NaN  28-FEB-18 12:05:11  ,3094242,  
4        NaN         NaN              NaN  28-FEB-18 12:05:11  ,2526331,

In [ ]:
dftrips_fresh[dftrips_fresh['LINEID'] == '46A'][dftrips_fresh['DIRECTION'] == 1]['PLANNEDTIME_DEP'].unique()